# Config

In [1]:
from __future__ import print_function
from pyspark import SparkContext , SparkConf
import sys
from operator import add
from csv import reader
from pyspark.sql import SQLContext, SparkSession

In [2]:
import os

In [3]:
import json

In [4]:
from pyspark.sql.functions import col, lit

In [5]:
cf = SparkConf()
cf.set("spark.submit.deployMode","client")

sc = SparkContext.getOrCreate(cf)

spark = SparkSession.builder.appName("Cleaning_RDS").getOrCreate()

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
23/12/09 04:25:50 INFO org.apache.spark.SparkEnv: Registering MapOutputTracker
23/12/09 04:25:50 INFO org.apache.spark.SparkEnv: Registering BlockManagerMaster
23/12/09 04:25:50 INFO org.apache.spark.SparkEnv: Registering BlockManagerMasterHeartbeat
23/12/09 04:25:50 INFO org.apache.spark.SparkEnv: Registering OutputCommitCoordinator


In [6]:
pwd

'/home/dc5415_nyu_edu/Project/Code/Parsing'

In [14]:
!hdfs dfs -ls Project/Data/Format_data/

Found 36 items
drwxrwxrwx+  - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:52 Project/Data/Format_data/competitions.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:27 Project/Data/Format_data/event_50_50.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:29 Project/Data/Format_data/event_bad_behaviour.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-27 21:34 Project/Data/Format_data/event_ball_receipt.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-27 22:17 Project/Data/Format_data/event_ball_recovery.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:27 Project/Data/Format_data/event_block.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-27 21:51 Project/Data/Format_data/event_carry.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:42 Project/Data/Format_data/event_clearance.parquet
drwxr-xr-x   

In [7]:
new_data_dir = '/user/dc5415_nyu_edu/Project/Data/Format_data/'
new_data_dir

'/user/dc5415_nyu_edu/Project/Data/Format_data/'

# Adding pks to events and lineups file

## Events file

In [28]:
cluster_event_dir = '../../Data/data/events/'
new_cluster_event_dir = '../../Data/data/events_/'
os.makedirs(new_cluster_event_dir, exist_ok=True)

In [29]:
!ls ../../Data/data/

competitions.json  events  events_  lineups  matches  three-sixty


In [51]:
for file_ in os.listdir(cluster_event_dir):
    match_id = int(file_.split('.')[0])
    with open(os.path.join(cluster_event_dir,file_),'r') as f:
        z = json.load(f)
        for item in z:
            item["match_id"]=match_id
        with open(os.path.join(new_cluster_event_dir,file_),'w') as newf:
            json.dump(z, newf, indent = 4)

## Lineups file

In [52]:
cluster_lineups_dir = '../../Data/data/lineups/'
new_cluster_lineups_dir = '../../Data/data/lineups_/'
os.makedirs(new_cluster_lineups_dir, exist_ok=True)

In [29]:
!ls ../../Data/data/

competitions.json  events  events_  lineups  matches  three-sixty


In [58]:
for file_ in os.listdir(cluster_lineups_dir):
    match_id = int(file_.split('.')[0])
    with open(os.path.join(cluster_lineups_dir,file_),'r') as f:
        z = json.load(f)
        for item in z:
            item["match_id"]=match_id
        with open(os.path.join(new_cluster_lineups_dir,file_),'w') as newf:
            json.dump(z, newf, indent = 4)

# Competitions Data

In [7]:
file_path = "Project/Data/data/competitions.json"

In [8]:
comp_df = spark.read.option("multiline","true") \
      .json(file_path)
comp_df.show()

+------------------+--------------+-------------------------+----------------+-----------------+------------+--------------------+-------------------+--------------------+--------------------+---------+-----------+
|competition_gender|competition_id|competition_international|competition_name|competition_youth|country_name|     match_available|match_available_360|       match_updated|   match_updated_360|season_id|season_name|
+------------------+--------------+-------------------------+----------------+-----------------+------------+--------------------+-------------------+--------------------+--------------------+---------+-----------+
|              male|             9|                    false|   1. Bundesliga|            false|     Germany|2023-08-17T23:51:...|               null|2023-08-17T23:51:...|                null|       27|  2015/2016|
|              male|            16|                    false|Champions League|            false|      Europe|2023-03-07T12:20:...|          

In [9]:
comp_df.printSchema()

root
 |-- competition_gender: string (nullable = true)
 |-- competition_id: long (nullable = true)
 |-- competition_international: boolean (nullable = true)
 |-- competition_name: string (nullable = true)
 |-- competition_youth: boolean (nullable = true)
 |-- country_name: string (nullable = true)
 |-- match_available: string (nullable = true)
 |-- match_available_360: string (nullable = true)
 |-- match_updated: string (nullable = true)
 |-- match_updated_360: string (nullable = true)
 |-- season_id: long (nullable = true)
 |-- season_name: string (nullable = true)



In [13]:
comp_df.select('competition_id').distinct().count()

18

In [14]:
comp_df.select('competition_id','season_id').distinct().count()

67

## Saving competititon data as parquet

In [16]:
!hdfs dfs -mkdir Project/Data/Format_data/

In [20]:
!hdfs dfs -ls Project/Data/

Found 8 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       6148 2023-11-14 20:42 Project/Data/.DS_Store
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:43 Project/Data/Format_data
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu     165130 2023-11-14 20:42 Project/Data/LICENSE.pdf
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       1753 2023-11-14 20:42 Project/Data/README.md
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu 1166414322 2023-11-14 21:13 Project/Data/StatsbombData.zip
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 20:52 Project/Data/data
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 20:42 Project/Data/doc
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 20:42 Project/Data/img


In [21]:
comp_df.write.parquet(f"{new_data_dir}/competitions.parquet")

In [22]:
!hdfs dfs -ls Project/Data/Format_data

Found 1 items
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:52 Project/Data/Format_data/competitions.parquet


# Matches data

In [29]:
!hdfs dfs -ls Project/Data/data/matches

Found 18 items
drwxrwxrwx   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 20:52 Project/Data/data/matches/11
drwxrwxrwx   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 20:51 Project/Data/data/matches/116
drwxrwxrwx   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 20:52 Project/Data/data/matches/12
drwxrwxrwx   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 20:52 Project/Data/data/matches/1238
drwxrwxrwx   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 20:51 Project/Data/data/matches/1470
drwxrwxrwx   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 20:52 Project/Data/data/matches/16
drwxrwxrwx   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 20:52 Project/Data/data/matches/2
drwxrwxrwx   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 20:52 Project/Data/data/matches/35
drwxrwxrwx   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 20:52 Project/Data/data/matches/37
drwxrwxrwx   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11

In [15]:
file_path = "Project/Data/data/matches/*/*.json"

In [16]:
match_df = spark.read.option("multiline","true").json(file_path)

In [17]:
match_df.printSchema()

root
 |-- away_score: long (nullable = true)
 |-- away_team: struct (nullable = true)
 |    |-- away_team_gender: string (nullable = true)
 |    |-- away_team_group: string (nullable = true)
 |    |-- away_team_id: long (nullable = true)
 |    |-- away_team_name: string (nullable = true)
 |    |-- country: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |-- managers: array (nullable = true)
 |    |    |-- element: struct (containsNull = true)
 |    |    |    |-- country: struct (nullable = true)
 |    |    |    |    |-- id: long (nullable = true)
 |    |    |    |    |-- name: string (nullable = true)
 |    |    |    |-- dob: string (nullable = true)
 |    |    |    |-- id: long (nullable = true)
 |    |    |    |-- name: string (nullable = true)
 |    |    |    |-- nickname: string (nullable = true)
 |-- competition: struct (nullable = true)
 |    |-- competition_id: long (nullable = true)
 |    |-- competition_nam

In [18]:
cols_interest = ['away_score','away_team.away_team_gender','away_team.away_team_group','away_team.away_team_id',
                'away_team.away_team_name','away_team.managers.country.id',
                 'away_team.managers.country.name', 'away_team.managers.name',
                 'away_team.managers.dob','away_team.managers.id','away_team.managers.nickname',
                 'competition.competition_id','competition.competition_name','competition.country_name',
                 'competition_stage.id','competition_stage.name',
                 'home_score','home_team.home_team_gender','home_team.home_team_group',
                 'home_team.home_team_id',
                'home_team.home_team_name','home_team.managers.country.id',
                 'home_team.managers.country.name', 'home_team.managers.name',
                 'home_team.managers.dob','home_team.managers.id','home_team.managers.nickname',
                 'kick_off', 'last_updated','last_updated_360','match_date','match_id',
                 'match_status','match_status_360','match_week','referee.country.id','referee.country.name',
                'referee.id','referee.name','season.season_id','season.season_name','stadium.country.id','stadium.country.name',
                'stadium.id','stadium.name']

alias = [_.replace('.','_') for _ in cols_interest]

match_df_clean = match_df.select(*[col(n)[0].alias(a) if 'managers' in n else col(n).alias(a)
                           for n,a in zip(cols_interest,alias)])

In [19]:
match_df_clean.printSchema()

root
 |-- away_score: long (nullable = true)
 |-- away_team_away_team_gender: string (nullable = true)
 |-- away_team_away_team_group: string (nullable = true)
 |-- away_team_away_team_id: long (nullable = true)
 |-- away_team_away_team_name: string (nullable = true)
 |-- away_team_managers_country_id: long (nullable = true)
 |-- away_team_managers_country_name: string (nullable = true)
 |-- away_team_managers_name: string (nullable = true)
 |-- away_team_managers_dob: string (nullable = true)
 |-- away_team_managers_id: long (nullable = true)
 |-- away_team_managers_nickname: string (nullable = true)
 |-- competition_competition_id: long (nullable = true)
 |-- competition_competition_name: string (nullable = true)
 |-- competition_country_name: string (nullable = true)
 |-- competition_stage_id: long (nullable = true)
 |-- competition_stage_name: string (nullable = true)
 |-- home_score: long (nullable = true)
 |-- home_team_home_team_gender: string (nullable = true)
 |-- home_team_ho

In [20]:
match_df_clean.select('match_id').distinct().count()

3199

## Saving match data as parquet

In [31]:
!hdfs dfs -ls Project/Data/Format_data/

Found 2 items
drwxrwxrwx   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:52 Project/Data/Format_data/competitions.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 23:08 Project/Data/Format_data/matches.parquet


In [36]:
f"{new_data_dir}/matches.parquet"

'/user/dc5415_nyu_edu/Project/Data/Format_data//matches.parquet'

In [37]:
!hdfs dfs -rm -R /user/dc5415_nyu_edu/Project/Data/Format_data//matches.parquet
match_df_clean.write.parquet(f"{new_data_dir}/matches.parquet")

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/matches.parquet


# Events data

In [8]:
event_id_map = {'pass':30,'ball_receipt':42,'carry':43,'pressure':17,'ball_recovery':2,
               'duel':4, 'block':6,'goalkeeper':23,'dribble':14,'clearance':9,
                'shot':16,'miscontrol':38,'foul_won':21 ,'foul_committed':22,
                'interception':10,'substitution':19,'half_end':34,'half_start':18,'injury_stoppage':40,
               '50_50':33,'tactics':36,'player_off':27,'bad_behaviour':24, 'error':37,'offside':8,
               'ref_ball_drop':41,'og_agnst':20,'og_for':25,'dispossesed':3,
               'start_xi':35, 'player_on':26, 'shield':28,'dribble_past':39}
print("Number of events: ", len(event_id_map))

Number of events:  33


In [9]:
gen_attrs = ['match_id','id','index','period','timestamp','minute',
'second','type','possession','possession_team','play_pattern','team','player',
'position','location','duration','under_pressure','off_camera','out','related_events']
print("Number of general attributes: ", len(gen_attrs))

Number of general attributes:  20


In [10]:
gen_attr_schema = ['match_id','id','index','period','timestamp','minute','second','type.id','type.name','possession','possession_team.id',
'possession_team.name', 'play_pattern.id','play_pattern.name','team.id','team.name',
'player.id','player.name','position.id','position.name','location','duration','under_pressure','off_camera',
'out','related_events']

In [11]:
file_path = "Project/Data/data/events_/*.json"

In [6]:
# edited_file_path = "Project/Data/data/events_/"

In [12]:
event_df = spark.read.option("multiline","true").json(file_path)

In [21]:
event_df.count()

11238057

In [23]:
event_df.printSchema()

root
 |-- 50_50: struct (nullable = true)
 |    |-- outcome: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |-- bad_behaviour: struct (nullable = true)
 |    |-- card: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |-- ball_receipt: struct (nullable = true)
 |    |-- outcome: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |-- ball_recovery: struct (nullable = true)
 |    |-- offensive: boolean (nullable = true)
 |    |-- recovery_failure: boolean (nullable = true)
 |-- block: struct (nullable = true)
 |    |-- deflection: boolean (nullable = true)
 |    |-- offensive: boolean (nullable = true)
 |    |-- save_block: boolean (nullable = true)
 |-- carry: struct (nullable = true)
 |    |-- end_location: array (nullable = true)
 |    |    |-- element: double (containsNull = true)
 |-- clearan

In [13]:
alias = [_.replace('.','_') for _ in gen_attr_schema]

gen_event_df = event_df.select(*[col(n).alias(a) for n,a in zip(gen_attr_schema,alias)])

In [14]:
gen_event_df.printSchema()

root
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- duration: double (nullable = true)
 |-- under_pressure: boolean (nullable = true)
 |-- of

In [32]:
filename = f"{new_data_dir}event_general_attr.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_general_attr.parquet'

In [33]:
!hdfs dfs -rm -R $filename
gen_event_df.write.parquet(filename)

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_general_attr.parquet


## Pass - ID:30

In [34]:
event = 'pass'
id_ = event_id_map[event] 
event, id_

('pass', 30)

In [35]:
!hdfs dfs -ls Project/Data/data/events

Found 3199 items
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3256730 2023-11-14 20:58 Project/Data/data/events/15946.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2864428 2023-11-14 20:54 Project/Data/data/events/15956.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3013141 2023-11-14 21:09 Project/Data/data/events/15973.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3342666 2023-11-14 21:03 Project/Data/data/events/15978.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3380879 2023-11-14 21:00 Project/Data/data/events/15986.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3341389 2023-11-14 21:04 Project/Data/data/events/15998.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3106048 2023-11-14 20:57 Project/Data/data/events/16010.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3845714 2023-11-14 21:12 Project/Data/data/events/16023.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3100630 2023-11-14 21:06 Project/Data/data/events/16029.json
-r

-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2953527 2023-11-14 21:10 Project/Data/data/events/19822.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3181099 2023-11-14 21:10 Project/Data/data/events/2275026.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2647115 2023-11-14 20:56 Project/Data/data/events/2275027.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3384761 2023-11-14 20:59 Project/Data/data/events/2275028.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2328897 2023-11-14 21:09 Project/Data/data/events/2275029.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2542666 2023-11-14 20:56 Project/Data/data/events/2275030.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2783749 2023-11-14 21:11 Project/Data/data/events/2275033.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3062591 2023-11-14 21:09 Project/Data/data/events/2275034.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2456443 2023-11-14 20:54 Project/Data/data/events/2275036.json
-rw

-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3066724 2023-11-14 21:08 Project/Data/data/events/3879585.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3054455 2023-11-14 21:01 Project/Data/data/events/3879586.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3243819 2023-11-14 20:53 Project/Data/data/events/3879587.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2782366 2023-11-14 20:59 Project/Data/data/events/3879588.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2429922 2023-11-14 21:13 Project/Data/data/events/3879589.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2936595 2023-11-14 21:10 Project/Data/data/events/3879590.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3089582 2023-11-14 20:57 Project/Data/data/events/3879591.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2980609 2023-11-14 20:52 Project/Data/data/events/3879592.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3757710 2023-11-14 20:55 Project/Data/data/events/3879593.json
-

In [36]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
pass_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
pass_event_df.printSchema()

root
 |-- pass: struct (nullable = true)
 |    |-- aerial_won: boolean (nullable = true)
 |    |-- angle: double (nullable = true)
 |    |-- assisted_shot_id: string (nullable = true)
 |    |-- backheel: boolean (nullable = true)
 |    |-- body_part: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |-- cross: boolean (nullable = true)
 |    |-- cut_back: boolean (nullable = true)
 |    |-- deflected: boolean (nullable = true)
 |    |-- end_location: array (nullable = true)
 |    |    |-- element: double (containsNull = true)
 |    |-- goal_assist: boolean (nullable = true)
 |    |-- height: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |-- inswinging: boolean (nullable = true)
 |    |-- length: double (nullable = true)
 |    |-- miscommunication: boolean (nullable = true)
 |    |-- no_touch: boolean (nullable = true)
 |    |-- outcome: struct (n

In [37]:
cols_interest = ['pass.aerial_won','pass.angle','pass.assisted_shot_id','pass.body_part.id',
                 'pass.body_part.name','pass.cross','pass.cut_back',
'pass.deflected','pass.end_location','pass.goal_assist','pass.height.id','pass.height.name',
                 'pass.inswinging','pass.length','pass.miscommunication','pass.no_touch','pass.outcome.id',
                 'pass.outcome.name','pass.recipient.id','pass.recipient.name','pass.shot_assist',
'pass.straight','pass.switch','pass.technique.id','pass.technique.name','pass.through_ball','pass.type.id',
                 'pass.type.name'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

pass_event_df_clean = pass_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

pass_event_df_clean.printSchema()

root
 |-- pass_aerial_won: boolean (nullable = true)
 |-- pass_angle: double (nullable = true)
 |-- pass_assisted_shot_id: string (nullable = true)
 |-- pass_body_part_id: long (nullable = true)
 |-- pass_body_part_name: string (nullable = true)
 |-- pass_cross: boolean (nullable = true)
 |-- pass_cut_back: boolean (nullable = true)
 |-- pass_deflected: boolean (nullable = true)
 |-- pass_end_location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- pass_goal_assist: boolean (nullable = true)
 |-- pass_height_id: long (nullable = true)
 |-- pass_height_name: string (nullable = true)
 |-- pass_inswinging: boolean (nullable = true)
 |-- pass_length: double (nullable = true)
 |-- pass_miscommunication: boolean (nullable = true)
 |-- pass_no_touch: boolean (nullable = true)
 |-- pass_outcome_id: long (nullable = true)
 |-- pass_outcome_name: string (nullable = true)
 |-- pass_recipient_id: long (nullable = true)
 |-- pass_recipient_name: string (nullable = true

### Saving pass event data as parquet

In [38]:
!hdfs dfs -ls Project/Data/Format_data/

Found 36 items
drwxrwxrwx+  - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:52 Project/Data/Format_data/competitions.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:27 Project/Data/Format_data/event_50_50.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:29 Project/Data/Format_data/event_bad_behaviour.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-27 21:34 Project/Data/Format_data/event_ball_receipt.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-27 22:17 Project/Data/Format_data/event_ball_recovery.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:27 Project/Data/Format_data/event_block.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-27 21:51 Project/Data/Format_data/event_carry.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:42 Project/Data/Format_data/event_clearance.parquet
drwxr-xr-x   

In [39]:
f"{new_data_dir}event_{event}.parquet"

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_pass.parquet'

In [40]:
!hdfs dfs -rm -R /user/dc5415_nyu_edu/Project/Data/Format_data/event_pass.parquet
pass_event_df_clean.write.parquet(f"{new_data_dir}event_{event}.parquet")

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_pass.parquet


In [41]:
!hdfs dfs -ls Project/Data/Format_data/event_pass.parquet

Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:57 Project/Data/Format_data/event_pass.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    2405125 2023-12-06 20:57 Project/Data/Format_data/event_pass.parquet/part-00000-59df4e60-4b71-499c-b790-2e64d8e788aa-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    2294062 2023-12-06 20:57 Project/Data/Format_data/event_pass.parquet/part-00001-59df4e60-4b71-499c-b790-2e64d8e788aa-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    2373976 2023-12-06 20:57 Project/Data/Format_data/event_pass.parquet/part-00002-59df4e60-4b71-499c-b790-2e64d8e788aa-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    2404124 2023-12-06 20:57 Project/Data/Format_data/event_pass.parquet/part-00003-59df4e60-4b71-499c-b790-2e64d8e788aa-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    2327906 2023-12-06 20:57 Project/Data/Format_data/event_pass.parquet/p

-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    1967497 2023-12-06 20:57 Project/Data/Format_data/event_pass.parquet/part-00191-59df4e60-4b71-499c-b790-2e64d8e788aa-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    1986504 2023-12-06 20:57 Project/Data/Format_data/event_pass.parquet/part-00192-59df4e60-4b71-499c-b790-2e64d8e788aa-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    1956733 2023-12-06 20:57 Project/Data/Format_data/event_pass.parquet/part-00193-59df4e60-4b71-499c-b790-2e64d8e788aa-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    1949478 2023-12-06 20:57 Project/Data/Format_data/event_pass.parquet/part-00194-59df4e60-4b71-499c-b790-2e64d8e788aa-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    1908822 2023-12-06 20:57 Project/Data/Format_data/event_pass.parquet/part-00195-59df4e60-4b71-499c-b790-2e64d8e788aa-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    1930495 2023-12-06 20:57 Pr

## Ball Receipt - ID:42

In [42]:
event = 'ball_receipt'
id_ = event_id_map[event] 
event, id_

('ball_receipt', 42)

In [43]:
!hdfs dfs -ls Project/Data/data/events

Found 3199 items
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3256730 2023-11-14 20:58 Project/Data/data/events/15946.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2864428 2023-11-14 20:54 Project/Data/data/events/15956.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3013141 2023-11-14 21:09 Project/Data/data/events/15973.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3342666 2023-11-14 21:03 Project/Data/data/events/15978.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3380879 2023-11-14 21:00 Project/Data/data/events/15986.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3341389 2023-11-14 21:04 Project/Data/data/events/15998.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3106048 2023-11-14 20:57 Project/Data/data/events/16010.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3845714 2023-11-14 21:12 Project/Data/data/events/16023.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3100630 2023-11-14 21:06 Project/Data/data/events/16029.json
-r

-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2771059 2023-11-14 20:55 Project/Data/data/events/3754013.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2661703 2023-11-14 21:12 Project/Data/data/events/3754014.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3125815 2023-11-14 21:10 Project/Data/data/events/3754015.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2947287 2023-11-14 21:05 Project/Data/data/events/3754016.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2706020 2023-11-14 21:00 Project/Data/data/events/3754017.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3492950 2023-11-14 21:09 Project/Data/data/events/3754018.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3083768 2023-11-14 21:06 Project/Data/data/events/3754019.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3001143 2023-11-14 21:08 Project/Data/data/events/3754020.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3096545 2023-11-14 21:05 Project/Data/data/events/3754021.json
-

-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3019237 2023-11-14 20:54 Project/Data/data/events/69242.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3277175 2023-11-14 21:11 Project/Data/data/events/69243.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3410047 2023-11-14 21:10 Project/Data/data/events/69244.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3247677 2023-11-14 21:03 Project/Data/data/events/69245.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3096138 2023-11-14 21:05 Project/Data/data/events/69246.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3305875 2023-11-14 21:04 Project/Data/data/events/69247.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3248278 2023-11-14 21:01 Project/Data/data/events/69248.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3134964 2023-11-14 20:52 Project/Data/data/events/69249.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2706160 2023-11-14 21:10 Project/Data/data/events/69250.json
-rwxrwxrwx+  1 dc54

In [44]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
ball_recpt_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
ball_recpt_event_df.printSchema()

root
 |-- ball_receipt: struct (nullable = true)
 |    |-- outcome: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- 

In [45]:
cols_interest = ['ball_receipt.outcome.id','ball_receipt.outcome.name'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

ball_recpt_event_df_clean = ball_recpt_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

ball_recpt_event_df_clean.printSchema()

root
 |-- ball_receipt_outcome_id: long (nullable = true)
 |-- ball_receipt_outcome_name: string (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (conta

### Saving ball receipt event data as parquet

In [46]:
!hdfs dfs -ls Project/Data/Format_data/

Found 36 items
drwxrwxrwx+  - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:52 Project/Data/Format_data/competitions.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:27 Project/Data/Format_data/event_50_50.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:29 Project/Data/Format_data/event_bad_behaviour.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-27 21:34 Project/Data/Format_data/event_ball_receipt.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-27 22:17 Project/Data/Format_data/event_ball_recovery.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:27 Project/Data/Format_data/event_block.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-27 21:51 Project/Data/Format_data/event_carry.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:42 Project/Data/Format_data/event_clearance.parquet
drwxr-xr-x   

In [47]:
f"{new_data_dir}event_{event}.parquet"

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_ball_receipt.parquet'

In [48]:
!hdfs dfs -rm -R /user/dc5415_nyu_edu/Project/Data/Format_data/event_ball_receipt.parquet
ball_recpt_event_df_clean.write.parquet(f"{new_data_dir}event_{event}.parquet")

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_ball_receipt.parquet


23/12/06 20:58:00 WARN org.apache.spark.deploy.yarn.YarnAllocator: Container from a bad node: container_e02_1691775874963_39387_01_000005 on host: nyu-dataproc-sw-x58r.c.hpc-dataproc-19b8.internal. Exit status: 143. Diagnostics: [2023-12-06 20:58:00.496]Container killed on request. Exit code is 143
[2023-12-06 20:58:00.496]Container exited with a non-zero exit code 143. 
[2023-12-06 20:58:00.497]Killed by external signal
.
23/12/06 20:58:00 WARN org.apache.spark.scheduler.cluster.YarnSchedulerBackend$YarnSchedulerEndpoint: Requesting driver to remove executor 3 for reason Container from a bad node: container_e02_1691775874963_39387_01_000005 on host: nyu-dataproc-sw-x58r.c.hpc-dataproc-19b8.internal. Exit status: 143. Diagnostics: [2023-12-06 20:58:00.496]Container killed on request. Exit code is 143
[2023-12-06 20:58:00.496]Container exited with a non-zero exit code 143. 
[2023-12-06 20:58:00.497]Killed by external signal
.
23/12/06 20:58:00 ERROR org.apache.spark.scheduler.cluster.Ya

In [49]:
!hdfs dfs -ls Project/Data/Format_data/event_ball_receipt.parquet

Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:58 Project/Data/Format_data/event_ball_receipt.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    1653790 2023-12-06 20:57 Project/Data/Format_data/event_ball_receipt.parquet/part-00000-2d4f6bbc-acef-4cd0-af45-12d8ece2a300-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    1528534 2023-12-06 20:57 Project/Data/Format_data/event_ball_receipt.parquet/part-00001-2d4f6bbc-acef-4cd0-af45-12d8ece2a300-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    1659940 2023-12-06 20:57 Project/Data/Format_data/event_ball_receipt.parquet/part-00002-2d4f6bbc-acef-4cd0-af45-12d8ece2a300-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    1632473 2023-12-06 20:57 Project/Data/Format_data/event_ball_receipt.parquet/part-00003-2d4f6bbc-acef-4cd0-af45-12d8ece2a300-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    1590263 2023-12-06 20:57 Proje

## Carry - ID:43

In [50]:
event = 'carry'
id_ = event_id_map[event] 
event, id_

('carry', 43)

In [51]:
!hdfs dfs -ls Project/Data/data/events

Found 3199 items
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3256730 2023-11-14 20:58 Project/Data/data/events/15946.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2864428 2023-11-14 20:54 Project/Data/data/events/15956.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3013141 2023-11-14 21:09 Project/Data/data/events/15973.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3342666 2023-11-14 21:03 Project/Data/data/events/15978.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3380879 2023-11-14 21:00 Project/Data/data/events/15986.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3341389 2023-11-14 21:04 Project/Data/data/events/15998.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3106048 2023-11-14 20:57 Project/Data/data/events/16010.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3845714 2023-11-14 21:12 Project/Data/data/events/16023.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3100630 2023-11-14 21:06 Project/Data/data/events/16029.json
-r

-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2908876 2023-11-14 21:05 Project/Data/data/events/3775618.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2743925 2023-11-14 21:05 Project/Data/data/events/3775619.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2908605 2023-11-14 21:08 Project/Data/data/events/3775620.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2875662 2023-11-14 20:55 Project/Data/data/events/3775621.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2811831 2023-11-14 20:55 Project/Data/data/events/3775622.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2583202 2023-11-14 21:11 Project/Data/data/events/3775623.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2740860 2023-11-14 21:03 Project/Data/data/events/3775624.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2986533 2023-11-14 21:11 Project/Data/data/events/3775625.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3403808 2023-11-14 21:11 Project/Data/data/events/3775626.json
-

In [52]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
carry_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
carry_event_df.printSchema()

root
 |-- carry: struct (nullable = true)
 |    |-- end_location: array (nullable = true)
 |    |    |-- element: double (containsNull = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- n

In [53]:
cols_interest = ['carry.end_location'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

carry_event_df_clean = carry_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

carry_event_df_clean.printSchema()

root
 |-- carry_end_location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsNull = tru

### Saving carry event data as parquet

In [54]:
!hdfs dfs -ls Project/Data/Format_data/

Found 36 items
drwxrwxrwx+  - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:52 Project/Data/Format_data/competitions.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:27 Project/Data/Format_data/event_50_50.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:29 Project/Data/Format_data/event_bad_behaviour.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:58 Project/Data/Format_data/event_ball_receipt.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-27 22:17 Project/Data/Format_data/event_ball_recovery.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:27 Project/Data/Format_data/event_block.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-27 21:51 Project/Data/Format_data/event_carry.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:42 Project/Data/Format_data/event_clearance.parquet
drwxr-xr-x   

In [55]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_carry.parquet'

In [56]:
!hdfs dfs -rm -R $filename
carry_event_df_clean.write.parquet(filename)

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_carry.parquet


In [57]:
!hdfs dfs -ls $filename

Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 /user/dc5415_nyu_edu/Project/Data/Format_data/event_carry.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    2232463 2023-12-06 20:58 /user/dc5415_nyu_edu/Project/Data/Format_data/event_carry.parquet/part-00000-5f891c23-dd9f-48d7-988b-5ba2787b6298-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    2089999 2023-12-06 20:58 /user/dc5415_nyu_edu/Project/Data/Format_data/event_carry.parquet/part-00001-5f891c23-dd9f-48d7-988b-5ba2787b6298-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    2281148 2023-12-06 20:58 /user/dc5415_nyu_edu/Project/Data/Format_data/event_carry.parquet/part-00002-5f891c23-dd9f-48d7-988b-5ba2787b6298-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu    2186625 2023-12-06 20:58 /user/dc5415_nyu_edu/Project/Data/Format_data/event_carry.parquet/part-00003-5f891c23-dd9f-48d7-988b-5ba2787b6298-c000.snappy.parquet
-rw-r--r

## Ball Recovery - ID:2

In [58]:
event = 'ball_recovery'
id_ = event_id_map[event] 
event, id_

('ball_recovery', 2)

In [59]:
!hdfs dfs -ls Project/Data/data/events

Found 3199 items
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3256730 2023-11-14 20:58 Project/Data/data/events/15946.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2864428 2023-11-14 20:54 Project/Data/data/events/15956.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3013141 2023-11-14 21:09 Project/Data/data/events/15973.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3342666 2023-11-14 21:03 Project/Data/data/events/15978.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3380879 2023-11-14 21:00 Project/Data/data/events/15986.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3341389 2023-11-14 21:04 Project/Data/data/events/15998.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3106048 2023-11-14 20:57 Project/Data/data/events/16010.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3845714 2023-11-14 21:12 Project/Data/data/events/16023.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3100630 2023-11-14 21:06 Project/Data/data/events/16029.json
-r

-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2745450 2023-11-14 21:09 Project/Data/data/events/3825775.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2974089 2023-11-14 20:59 Project/Data/data/events/3825776.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2653748 2023-11-14 20:56 Project/Data/data/events/3825777.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2820523 2023-11-14 21:06 Project/Data/data/events/3825778.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2738460 2023-11-14 21:08 Project/Data/data/events/3825779.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2999015 2023-11-14 21:04 Project/Data/data/events/3825780.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2504615 2023-11-14 21:01 Project/Data/data/events/3825781.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3100471 2023-11-14 21:00 Project/Data/data/events/3825782.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2646912 2023-11-14 20:55 Project/Data/data/events/3825783.json
-

In [60]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
ball_rec_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
ball_rec_event_df.printSchema()

root
 |-- ball_recovery: struct (nullable = true)
 |    |-- offensive: boolean (nullable = true)
 |    |-- recovery_failure: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id: long (nullable = true)
 | 

In [61]:
cols_interest = ['ball_recovery.offensive','ball_recovery.recovery_failure'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

ball_rec_event_df_clean = ball_rec_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

ball_rec_event_df_clean.printSchema()

root
 |-- ball_recovery_offensive: boolean (nullable = true)
 |-- ball_recovery_recovery_failure: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: doub

### Saving ball recovery event data as parquet

In [62]:
!hdfs dfs -ls Project/Data/Format_data/

Found 36 items
drwxrwxrwx+  - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:52 Project/Data/Format_data/competitions.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:27 Project/Data/Format_data/event_50_50.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:29 Project/Data/Format_data/event_bad_behaviour.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:58 Project/Data/Format_data/event_ball_receipt.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-27 22:17 Project/Data/Format_data/event_ball_recovery.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:27 Project/Data/Format_data/event_block.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_carry.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:42 Project/Data/Format_data/event_clearance.parquet
drwxr-xr-x   

In [63]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_ball_recovery.parquet'

In [64]:
!hdfs dfs -rm -R $filename
ball_rec_event_df_clean.write.parquet(filename)

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_ball_recovery.parquet


In [65]:
!hdfs dfs -ls $filename

Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 /user/dc5415_nyu_edu/Project/Data/Format_data/event_ball_recovery.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu     125810 2023-12-06 20:59 /user/dc5415_nyu_edu/Project/Data/Format_data/event_ball_recovery.parquet/part-00000-6f7eec3b-1062-49ea-8ca0-55c171a917a2-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu     146058 2023-12-06 20:59 /user/dc5415_nyu_edu/Project/Data/Format_data/event_ball_recovery.parquet/part-00001-6f7eec3b-1062-49ea-8ca0-55c171a917a2-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu     134086 2023-12-06 20:59 /user/dc5415_nyu_edu/Project/Data/Format_data/event_ball_recovery.parquet/part-00002-6f7eec3b-1062-49ea-8ca0-55c171a917a2-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu     137778 2023-12-06 20:59 /user/dc5415_nyu_edu/Project/Data/Format_data/event_ball_recovery.parquet/part-00003-6f7eec3b-1062-49ea-8ca0-5

## Duel - ID:4

In [66]:
event = 'duel'
id_ = event_id_map[event] 
event, id_

('duel', 4)

In [67]:
!hdfs dfs -ls Project/Data/data/events

Found 3199 items
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3256730 2023-11-14 20:58 Project/Data/data/events/15946.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2864428 2023-11-14 20:54 Project/Data/data/events/15956.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3013141 2023-11-14 21:09 Project/Data/data/events/15973.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3342666 2023-11-14 21:03 Project/Data/data/events/15978.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3380879 2023-11-14 21:00 Project/Data/data/events/15986.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3341389 2023-11-14 21:04 Project/Data/data/events/15998.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3106048 2023-11-14 20:57 Project/Data/data/events/16010.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3845714 2023-11-14 21:12 Project/Data/data/events/16023.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3100630 2023-11-14 21:06 Project/Data/data/events/16029.json
-r

-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3001669 2023-11-14 21:08 Project/Data/data/events/3829418.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3012116 2023-11-14 21:02 Project/Data/data/events/3829419.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3040185 2023-11-14 21:07 Project/Data/data/events/3829420.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2997731 2023-11-14 20:54 Project/Data/data/events/3829421.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3318539 2023-11-14 20:53 Project/Data/data/events/3829422.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2880738 2023-11-14 20:57 Project/Data/data/events/3829423.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2737439 2023-11-14 21:03 Project/Data/data/events/3829424.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3104845 2023-11-14 21:04 Project/Data/data/events/3829425.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2641221 2023-11-14 21:08 Project/Data/data/events/3829426.json
-

In [68]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
duel_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
duel_event_df.printSchema()

root
 |-- duel: struct (nullable = true)
 |    |-- outcome: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |-- type: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |   

In [69]:
cols_interest = ['duel.outcome.id','duel.outcome.name',
                 'duel.type.id','duel.type.name',] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

duel_event_df_clean = duel_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

duel_event_df_clean.printSchema()

root
 |-- duel_outcome_id: long (nullable = true)
 |-- duel_outcome_name: string (nullable = true)
 |-- duel_type_id: long (nullable = true)
 |-- duel_type_name: string (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)

### Saving duel event data as parquet

In [70]:
!hdfs dfs -ls Project/Data/Format_data/

Found 36 items
drwxrwxrwx+  - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:52 Project/Data/Format_data/competitions.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:27 Project/Data/Format_data/event_50_50.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:29 Project/Data/Format_data/event_bad_behaviour.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:58 Project/Data/Format_data/event_ball_receipt.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_ball_recovery.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:27 Project/Data/Format_data/event_block.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_carry.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:42 Project/Data/Format_data/event_clearance.parquet
drwxr-xr-x   

In [71]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_duel.parquet'

In [72]:
!hdfs dfs -rm -R $filename
duel_event_df_clean.write.parquet(filename)

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_duel.parquet


In [73]:
!hdfs dfs -ls $filename

Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 /user/dc5415_nyu_edu/Project/Data/Format_data/event_duel.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu     115795 2023-12-06 20:59 /user/dc5415_nyu_edu/Project/Data/Format_data/event_duel.parquet/part-00000-12ea8da8-0975-4e34-b925-7e8d993b84f8-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu     123991 2023-12-06 20:59 /user/dc5415_nyu_edu/Project/Data/Format_data/event_duel.parquet/part-00001-12ea8da8-0975-4e34-b925-7e8d993b84f8-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu     106187 2023-12-06 20:59 /user/dc5415_nyu_edu/Project/Data/Format_data/event_duel.parquet/part-00002-12ea8da8-0975-4e34-b925-7e8d993b84f8-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu     109701 2023-12-06 20:59 /user/dc5415_nyu_edu/Project/Data/Format_data/event_duel.parquet/part-00003-12ea8da8-0975-4e34-b925-7e8d993b84f8-c000.snappy.parquet
-rw-r--r--   

## Block - ID:6

In [74]:
event = 'block'
id_ = event_id_map[event] 
event, id_

('block', 6)

In [75]:
!hdfs dfs -ls Project/Data/data/events

Found 3199 items
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3256730 2023-11-14 20:58 Project/Data/data/events/15946.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2864428 2023-11-14 20:54 Project/Data/data/events/15956.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3013141 2023-11-14 21:09 Project/Data/data/events/15973.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3342666 2023-11-14 21:03 Project/Data/data/events/15978.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3380879 2023-11-14 21:00 Project/Data/data/events/15986.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3341389 2023-11-14 21:04 Project/Data/data/events/15998.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3106048 2023-11-14 20:57 Project/Data/data/events/16010.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3845714 2023-11-14 21:12 Project/Data/data/events/16023.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3100630 2023-11-14 21:06 Project/Data/data/events/16029.json
-r

-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2819624 2023-11-14 21:10 Project/Data/data/events/19806.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3311177 2023-11-14 21:10 Project/Data/data/events/19807.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2756456 2023-11-14 21:12 Project/Data/data/events/19808.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2665557 2023-11-14 21:10 Project/Data/data/events/19809.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2615026 2023-11-14 20:57 Project/Data/data/events/19810.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2871989 2023-11-14 21:02 Project/Data/data/events/19811.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2858075 2023-11-14 21:06 Project/Data/data/events/19813.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2955183 2023-11-14 20:55 Project/Data/data/events/19814.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3102637 2023-11-14 21:12 Project/Data/data/events/19815.json
-rwxrwxrwx+  1 dc54

-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2844042 2023-11-14 21:08 Project/Data/data/events/3825815.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2730443 2023-11-14 21:09 Project/Data/data/events/3825816.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2690181 2023-11-14 20:52 Project/Data/data/events/3825817.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2899002 2023-11-14 20:53 Project/Data/data/events/3825818.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3186538 2023-11-14 21:11 Project/Data/data/events/3825819.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3086414 2023-11-14 20:59 Project/Data/data/events/3825820.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2940042 2023-11-14 20:58 Project/Data/data/events/3825821.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3274291 2023-11-14 21:07 Project/Data/data/events/3825822.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2847301 2023-11-14 20:52 Project/Data/data/events/3825823.json
-

In [76]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
block_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
block_event_df.printSchema()

root
 |-- block: struct (nullable = true)
 |    |-- deflection: boolean (nullable = true)
 |    |-- offensive: boolean (nullable = true)
 |    |-- save_block: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    

In [77]:
cols_interest = ['block.deflection','block.offensive',
                 'block.save_block'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

block_event_df_clean = block_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

block_event_df_clean.printSchema()

root
 |-- block_deflection: boolean (nullable = true)
 |-- block_offensive: boolean (nullable = true)
 |-- block_save_block: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = tr

### Saving block event data as parquet

In [78]:
!hdfs dfs -ls Project/Data/Format_data/

Found 36 items
drwxrwxrwx+  - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:52 Project/Data/Format_data/competitions.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:27 Project/Data/Format_data/event_50_50.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:29 Project/Data/Format_data/event_bad_behaviour.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:58 Project/Data/Format_data/event_ball_receipt.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_ball_recovery.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:27 Project/Data/Format_data/event_block.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_carry.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:42 Project/Data/Format_data/event_clearance.parquet
drwxr-xr-x   

In [79]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_block.parquet'

In [80]:
!hdfs dfs -rm -R $filename
block_event_df_clean.write.parquet(filename)

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_block.parquet


In [81]:
!hdfs dfs -ls $filename

Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:00 /user/dc5415_nyu_edu/Project/Data/Format_data/event_block.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      75014 2023-12-06 21:00 /user/dc5415_nyu_edu/Project/Data/Format_data/event_block.parquet/part-00000-c110fe8c-9b1d-4eba-9c37-dff1365f3cbf-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      70468 2023-12-06 21:00 /user/dc5415_nyu_edu/Project/Data/Format_data/event_block.parquet/part-00001-c110fe8c-9b1d-4eba-9c37-dff1365f3cbf-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      64126 2023-12-06 21:00 /user/dc5415_nyu_edu/Project/Data/Format_data/event_block.parquet/part-00002-c110fe8c-9b1d-4eba-9c37-dff1365f3cbf-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      74963 2023-12-06 21:00 /user/dc5415_nyu_edu/Project/Data/Format_data/event_block.parquet/part-00003-c110fe8c-9b1d-4eba-9c37-dff1365f3cbf-c000.snappy.parquet
-rw-r--r

## GoalKeeper - ID:23

In [82]:
event = 'goalkeeper'
id_ = event_id_map[event] 
event, id_

('goalkeeper', 23)

In [83]:
!hdfs dfs -ls Project/Data/data/events

Found 3199 items
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3256730 2023-11-14 20:58 Project/Data/data/events/15946.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2864428 2023-11-14 20:54 Project/Data/data/events/15956.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3013141 2023-11-14 21:09 Project/Data/data/events/15973.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3342666 2023-11-14 21:03 Project/Data/data/events/15978.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3380879 2023-11-14 21:00 Project/Data/data/events/15986.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3341389 2023-11-14 21:04 Project/Data/data/events/15998.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3106048 2023-11-14 20:57 Project/Data/data/events/16010.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3845714 2023-11-14 21:12 Project/Data/data/events/16023.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3100630 2023-11-14 21:06 Project/Data/data/events/16029.json
-r

-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3102637 2023-11-14 21:12 Project/Data/data/events/19815.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3257502 2023-11-14 21:04 Project/Data/data/events/19816.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3098422 2023-11-14 21:12 Project/Data/data/events/19817.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3052177 2023-11-14 21:03 Project/Data/data/events/19818.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2804878 2023-11-14 20:59 Project/Data/data/events/19819.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2870021 2023-11-14 21:10 Project/Data/data/events/19820.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3130377 2023-11-14 21:01 Project/Data/data/events/19821.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2953527 2023-11-14 21:10 Project/Data/data/events/19822.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3181099 2023-11-14 21:10 Project/Data/data/events/2275026.json
-rwxrwxrwx+  1 dc

-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3422468 2023-11-14 21:12 Project/Data/data/events/3879616.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2463390 2023-11-14 20:53 Project/Data/data/events/3879617.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3149062 2023-11-14 21:07 Project/Data/data/events/3879618.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2873828 2023-11-14 20:54 Project/Data/data/events/3879619.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3651121 2023-11-14 21:09 Project/Data/data/events/3879620.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2918958 2023-11-14 21:03 Project/Data/data/events/3879621.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2774486 2023-11-14 21:10 Project/Data/data/events/3879622.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3294100 2023-11-14 20:55 Project/Data/data/events/3879623.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3010435 2023-11-14 21:01 Project/Data/data/events/3879624.json
-

In [84]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
gk_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
gk_event_df.printSchema()

root
 |-- goalkeeper: struct (nullable = true)
 |    |-- body_part: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |-- end_location: array (nullable = true)
 |    |    |-- element: double (containsNull = true)
 |    |-- lost_in_play: boolean (nullable = true)
 |    |-- lost_out: boolean (nullable = true)
 |    |-- outcome: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |-- penalty_saved_to_post: boolean (nullable = true)
 |    |-- position: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |-- punched_out: boolean (nullable = true)
 |    |-- saved_to_post: boolean (nullable = true)
 |    |-- shot_saved_off_target: boolean (nullable = true)
 |    |-- shot_saved_to_post: boolean (nullable = true)
 |    |-- success_in_play: boolean (nullable = true)
 |    |-- success_out: boolean

In [85]:
cols_interest = ['goalkeeper.body_part.id','goalkeeper.body_part.name',
                 'goalkeeper.end_location','goalkeeper.lost_in_play','goalkeeper.lost_out',
                'goalkeeper.outcome.id','goalkeeper.outcome.name','goalkeeper.penalty_saved_to_post',
                'goalkeeper.position.id','goalkeeper.position.name', 'goalkeeper.punched_out',
                 'goalkeeper.saved_to_post','goalkeeper.shot_saved_off_target','goalkeeper.success_in_play',
                'goalkeeper.success_out', 'goalkeeper.technique.id','goalkeeper.technique.name',
                'goalkeeper.type.id','goalkeeper.type.name'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

gk_event_df_clean = gk_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

gk_event_df_clean.printSchema()

root
 |-- goalkeeper_body_part_id: long (nullable = true)
 |-- goalkeeper_body_part_name: string (nullable = true)
 |-- goalkeeper_end_location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- goalkeeper_lost_in_play: boolean (nullable = true)
 |-- goalkeeper_lost_out: boolean (nullable = true)
 |-- goalkeeper_outcome_id: long (nullable = true)
 |-- goalkeeper_outcome_name: string (nullable = true)
 |-- goalkeeper_penalty_saved_to_post: boolean (nullable = true)
 |-- goalkeeper_position_id: long (nullable = true)
 |-- goalkeeper_position_name: string (nullable = true)
 |-- goalkeeper_punched_out: boolean (nullable = true)
 |-- goalkeeper_saved_to_post: boolean (nullable = true)
 |-- goalkeeper_shot_saved_off_target: boolean (nullable = true)
 |-- goalkeeper_success_in_play: boolean (nullable = true)
 |-- goalkeeper_success_out: boolean (nullable = true)
 |-- goalkeeper_technique_id: long (nullable = true)
 |-- goalkeeper_technique_name: string (nullable = t

### Saving goalkeeper event data as parquet

In [86]:
!hdfs dfs -ls Project/Data/Format_data/

Found 36 items
drwxrwxrwx+  - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:52 Project/Data/Format_data/competitions.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:27 Project/Data/Format_data/event_50_50.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:29 Project/Data/Format_data/event_bad_behaviour.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:58 Project/Data/Format_data/event_ball_receipt.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_ball_recovery.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:00 Project/Data/Format_data/event_block.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_carry.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:42 Project/Data/Format_data/event_clearance.parquet
drwxr-xr-x   

In [87]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_goalkeeper.parquet'

In [88]:
!hdfs dfs -rm -R $filename
gk_event_df_clean.write.parquet(filename)

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_goalkeeper.parquet


In [89]:
!hdfs dfs -ls $filename

Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:00 /user/dc5415_nyu_edu/Project/Data/Format_data/event_goalkeeper.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      73582 2023-12-06 21:00 /user/dc5415_nyu_edu/Project/Data/Format_data/event_goalkeeper.parquet/part-00000-202cb353-2bf9-4495-a4c5-eb4606cfbe6d-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      70892 2023-12-06 21:00 /user/dc5415_nyu_edu/Project/Data/Format_data/event_goalkeeper.parquet/part-00001-202cb353-2bf9-4495-a4c5-eb4606cfbe6d-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      59507 2023-12-06 21:00 /user/dc5415_nyu_edu/Project/Data/Format_data/event_goalkeeper.parquet/part-00002-202cb353-2bf9-4495-a4c5-eb4606cfbe6d-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      59690 2023-12-06 21:00 /user/dc5415_nyu_edu/Project/Data/Format_data/event_goalkeeper.parquet/part-00003-202cb353-2bf9-4495-a4c5-eb4606cfbe6d-c00

## Dribble - ID:14

In [90]:
event = 'dribble'
id_ = event_id_map[event] 
event, id_

('dribble', 14)

In [91]:
!hdfs dfs -ls Project/Data/data/events

Found 3199 items
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3256730 2023-11-14 20:58 Project/Data/data/events/15946.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2864428 2023-11-14 20:54 Project/Data/data/events/15956.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3013141 2023-11-14 21:09 Project/Data/data/events/15973.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3342666 2023-11-14 21:03 Project/Data/data/events/15978.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3380879 2023-11-14 21:00 Project/Data/data/events/15986.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3341389 2023-11-14 21:04 Project/Data/data/events/15998.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3106048 2023-11-14 20:57 Project/Data/data/events/16010.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3845714 2023-11-14 21:12 Project/Data/data/events/16023.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3100630 2023-11-14 21:06 Project/Data/data/events/16029.json
-r

-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3155578 2023-11-14 20:53 Project/Data/data/events/19770.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3148269 2023-11-14 21:01 Project/Data/data/events/19771.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2897114 2023-11-14 20:53 Project/Data/data/events/19772.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3147001 2023-11-14 20:54 Project/Data/data/events/19773.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2836783 2023-11-14 21:04 Project/Data/data/events/19774.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3093064 2023-11-14 21:09 Project/Data/data/events/19775.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2993444 2023-11-14 21:04 Project/Data/data/events/19776.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2839757 2023-11-14 20:52 Project/Data/data/events/19777.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3509104 2023-11-14 20:54 Project/Data/data/events/19778.json
-rwxrwxrwx+  1 dc54

-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2787134 2023-11-14 20:58 Project/Data/data/events/3878554.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2888222 2023-11-14 21:10 Project/Data/data/events/3878555.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2872546 2023-11-14 21:04 Project/Data/data/events/3878556.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3106929 2023-11-14 20:56 Project/Data/data/events/3878557.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3515054 2023-11-14 21:01 Project/Data/data/events/3878558.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3068240 2023-11-14 21:00 Project/Data/data/events/3878559.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3009035 2023-11-14 20:53 Project/Data/data/events/3878592.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2664831 2023-11-14 20:59 Project/Data/data/events/3878593.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3048621 2023-11-14 21:01 Project/Data/data/events/3878594.json
-

In [92]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
dribble_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
dribble_event_df.printSchema()

root
 |-- dribble: struct (nullable = true)
 |    |-- no_touch: boolean (nullable = true)
 |    |-- nutmeg: boolean (nullable = true)
 |    |-- outcome: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |-- overrun: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = tr

In [93]:
cols_interest = ['dribble.no_touch','dribble.nutmeg',
                 'dribble.outcome.id','dribble.outcome.name','dribble.overrun'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

dribble_event_df_clean = dribble_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

dribble_event_df_clean.printSchema()

root
 |-- dribble_no_touch: boolean (nullable = true)
 |-- dribble_nutmeg: boolean (nullable = true)
 |-- dribble_outcome_id: long (nullable = true)
 |-- dribble_outcome_name: string (nullable = true)
 |-- dribble_overrun: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long 

### Saving dribble event data as parquet

In [94]:
!hdfs dfs -ls Project/Data/Format_data/

Found 36 items
drwxrwxrwx+  - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:52 Project/Data/Format_data/competitions.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:27 Project/Data/Format_data/event_50_50.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:29 Project/Data/Format_data/event_bad_behaviour.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:58 Project/Data/Format_data/event_ball_receipt.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_ball_recovery.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:00 Project/Data/Format_data/event_block.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_carry.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:42 Project/Data/Format_data/event_clearance.parquet
drwxr-xr-x   

In [95]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble.parquet'

In [96]:
!hdfs dfs -rm -R $filename
dribble_event_df_clean.write.parquet(filename)

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble.parquet


In [97]:
!hdfs dfs -ls $filename

Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:01 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      82985 2023-12-06 21:01 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble.parquet/part-00000-25cfd40a-418b-4623-8935-64a592fb5fed-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      81136 2023-12-06 21:01 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble.parquet/part-00001-25cfd40a-418b-4623-8935-64a592fb5fed-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      75082 2023-12-06 21:01 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble.parquet/part-00002-25cfd40a-418b-4623-8935-64a592fb5fed-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      76492 2023-12-06 21:01 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble.parquet/part-00003-25cfd40a-418b-4623-8935-64a592fb5fed-c000.snappy.parque

## Clearance - ID:9

In [98]:
event = 'clearance'
id_ = event_id_map[event] 
event, id_

('clearance', 9)

In [99]:
!hdfs dfs -ls Project/Data/data/events

Found 3199 items
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3256730 2023-11-14 20:58 Project/Data/data/events/15946.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2864428 2023-11-14 20:54 Project/Data/data/events/15956.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3013141 2023-11-14 21:09 Project/Data/data/events/15973.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3342666 2023-11-14 21:03 Project/Data/data/events/15978.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3380879 2023-11-14 21:00 Project/Data/data/events/15986.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3341389 2023-11-14 21:04 Project/Data/data/events/15998.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3106048 2023-11-14 20:57 Project/Data/data/events/16010.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3845714 2023-11-14 21:12 Project/Data/data/events/16023.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3100630 2023-11-14 21:06 Project/Data/data/events/16029.json
-r

-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2956205 2023-11-14 21:04 Project/Data/data/events/3754045.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3090587 2023-11-14 21:00 Project/Data/data/events/3754046.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3198595 2023-11-14 20:55 Project/Data/data/events/3754047.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3138027 2023-11-14 21:07 Project/Data/data/events/3754048.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2821088 2023-11-14 20:59 Project/Data/data/events/3754049.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2651996 2023-11-14 21:08 Project/Data/data/events/3754050.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2534084 2023-11-14 21:03 Project/Data/data/events/3754051.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2787730 2023-11-14 21:10 Project/Data/data/events/3754052.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3140969 2023-11-14 21:05 Project/Data/data/events/3754053.json
-

-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3099692 2023-11-14 21:06 Project/Data/data/events/69217.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3128251 2023-11-14 20:52 Project/Data/data/events/69218.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2945839 2023-11-14 21:01 Project/Data/data/events/69219.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3467632 2023-11-14 21:07 Project/Data/data/events/69220.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3501996 2023-11-14 21:02 Project/Data/data/events/69221.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2878397 2023-11-14 21:02 Project/Data/data/events/69222.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3180672 2023-11-14 21:13 Project/Data/data/events/69223.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    3237619 2023-11-14 21:05 Project/Data/data/events/69224.json
-rwxrwxrwx+  1 dc5415_nyu_edu dc5415_nyu_edu    2915936 2023-11-14 21:07 Project/Data/data/events/69225.json
-rwxrwxrwx+  1 dc54

In [100]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
clear_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
clear_event_df.printSchema()

root
 |-- clearance: struct (nullable = true)
 |    |-- aerial_won: boolean (nullable = true)
 |    |-- body_part: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |-- head: boolean (nullable = true)
 |    |-- left_foot: boolean (nullable = true)
 |    |-- other: boolean (nullable = true)
 |    |-- right_foot: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id:

In [101]:
cols_interest = ['clearance.aerial_won','clearance.body_part.id','clearance.body_part.name',
                 'clearance.head','clearance.left_foot','clearance.other', 'clearance.right_foot'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

clear_event_df_clean = clear_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

clear_event_df_clean.printSchema()

root
 |-- clearance_aerial_won: boolean (nullable = true)
 |-- clearance_body_part_id: long (nullable = true)
 |-- clearance_body_part_name: string (nullable = true)
 |-- clearance_head: boolean (nullable = true)
 |-- clearance_left_foot: boolean (nullable = true)
 |-- clearance_other: boolean (nullable = true)
 |-- clearance_right_foot: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nulla

### Saving clearance event data as parquet

In [102]:
!hdfs dfs -ls Project/Data/Format_data/

Found 36 items
drwxrwxrwx+  - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:52 Project/Data/Format_data/competitions.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:27 Project/Data/Format_data/event_50_50.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:29 Project/Data/Format_data/event_bad_behaviour.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:58 Project/Data/Format_data/event_ball_receipt.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_ball_recovery.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:00 Project/Data/Format_data/event_block.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_carry.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-28 20:42 Project/Data/Format_data/event_clearance.parquet
drwxr-xr-x   

In [103]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_clearance.parquet'

In [104]:
!hdfs dfs -rm -R $filename
clear_event_df_clean.write.parquet(filename)

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_clearance.parquet


In [105]:
!hdfs dfs -ls $filename

Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:01 /user/dc5415_nyu_edu/Project/Data/Format_data/event_clearance.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      75682 2023-12-06 21:01 /user/dc5415_nyu_edu/Project/Data/Format_data/event_clearance.parquet/part-00000-b90bace5-0c9a-4ae3-bf18-914ef6a3ec63-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      89830 2023-12-06 21:01 /user/dc5415_nyu_edu/Project/Data/Format_data/event_clearance.parquet/part-00001-b90bace5-0c9a-4ae3-bf18-914ef6a3ec63-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      72160 2023-12-06 21:01 /user/dc5415_nyu_edu/Project/Data/Format_data/event_clearance.parquet/part-00002-b90bace5-0c9a-4ae3-bf18-914ef6a3ec63-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      65870 2023-12-06 21:01 /user/dc5415_nyu_edu/Project/Data/Format_data/event_clearance.parquet/part-00003-b90bace5-0c9a-4ae3-bf18-914ef6a3ec63-c000.sna

## Shot - ID:6

In [106]:
event = 'shot'
id_ = event_id_map[event] 
event, id_

('shot', 16)

In [107]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
shot_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
shot_event_df.printSchema()

root
 |-- shot: struct (nullable = true)
 |    |-- aerial_won: boolean (nullable = true)
 |    |-- body_part: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |-- deflected: boolean (nullable = true)
 |    |-- end_location: array (nullable = true)
 |    |    |-- element: double (containsNull = true)
 |    |-- first_time: boolean (nullable = true)
 |    |-- follows_dribble: boolean (nullable = true)
 |    |-- freeze_frame: array (nullable = true)
 |    |    |-- element: struct (containsNull = true)
 |    |    |    |-- location: array (nullable = true)
 |    |    |    |    |-- element: double (containsNull = true)
 |    |    |    |-- player: struct (nullable = true)
 |    |    |    |    |-- id: long (nullable = true)
 |    |    |    |    |-- name: string (nullable = true)
 |    |    |    |-- position: struct (nullable = true)
 |    |    |    |    |-- id: long (nullable = true)
 |    |    |    |    |-- name: string (nul

In [108]:
cols_interest = ['shot.aerial_won','shot.follows_dribble',
                 'shot.kick_off','shot.one_on_one','shot.redirect','shot.saved_off_target','shot.saved_to_post',
                 'shot.key_pass_id','shot.end_location','shot.first_time','shot.open_goal',
                 'shot.statsbomb_xg','shot.deflected','shot.technique.id','shot.technique.name',
'shot.body_part.id','shot.body_part.name','shot.type.id','shot.type.name','shot.outcome.id','shot.outcome.name'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

shot_event_df_clean = shot_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

shot_event_df_clean.printSchema()

root
 |-- shot_aerial_won: boolean (nullable = true)
 |-- shot_follows_dribble: boolean (nullable = true)
 |-- shot_kick_off: boolean (nullable = true)
 |-- shot_one_on_one: boolean (nullable = true)
 |-- shot_redirect: boolean (nullable = true)
 |-- shot_saved_off_target: boolean (nullable = true)
 |-- shot_saved_to_post: boolean (nullable = true)
 |-- shot_key_pass_id: string (nullable = true)
 |-- shot_end_location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- shot_first_time: boolean (nullable = true)
 |-- shot_open_goal: boolean (nullable = true)
 |-- shot_statsbomb_xg: double (nullable = true)
 |-- shot_deflected: boolean (nullable = true)
 |-- shot_technique_id: long (nullable = true)
 |-- shot_technique_name: string (nullable = true)
 |-- shot_body_part_id: long (nullable = true)
 |-- shot_body_part_name: string (nullable = true)
 |-- shot_type_id: long (nullable = true)
 |-- shot_type_name: string (nullable = true)
 |-- shot_outcome_id: long (nu

### Saving shot event data as parquet

In [109]:
!hdfs dfs -ls Project/Data/Format_data/

Found 36 items
drwxrwxrwx+  - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:52 Project/Data/Format_data/competitions.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:27 Project/Data/Format_data/event_50_50.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:29 Project/Data/Format_data/event_bad_behaviour.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:58 Project/Data/Format_data/event_ball_receipt.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_ball_recovery.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:00 Project/Data/Format_data/event_block.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_carry.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:01 Project/Data/Format_data/event_clearance.parquet
drwxr-xr-x   

In [110]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_shot.parquet'

In [111]:
!hdfs dfs -rm -R $filename
shot_event_df_clean.write.parquet(filename)

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_shot.parquet


In [112]:
!hdfs dfs -ls $filename

Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_shot.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu     102172 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_shot.parquet/part-00000-fd81bc30-9c55-40d8-9e81-c6c4d7f248ad-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      95738 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_shot.parquet/part-00001-fd81bc30-9c55-40d8-9e81-c6c4d7f248ad-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      82898 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_shot.parquet/part-00002-fd81bc30-9c55-40d8-9e81-c6c4d7f248ad-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      81763 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_shot.parquet/part-00003-fd81bc30-9c55-40d8-9e81-c6c4d7f248ad-c000.snappy.parquet
-rw-r--r--   

-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu     100929 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_shot.parquet/part-00184-fd81bc30-9c55-40d8-9e81-c6c4d7f248ad-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu     101596 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_shot.parquet/part-00185-fd81bc30-9c55-40d8-9e81-c6c4d7f248ad-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      90362 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_shot.parquet/part-00186-fd81bc30-9c55-40d8-9e81-c6c4d7f248ad-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      95819 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_shot.parquet/part-00187-fd81bc30-9c55-40d8-9e81-c6c4d7f248ad-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      95497 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_shot.parquet/part-00188-fd81bc30-9c55-40d8-9e81-c6c

## Miscontrol - ID:38

In [113]:
event = 'miscontrol'
id_ = event_id_map[event] 
event, id_

('miscontrol', 38)

In [114]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
miscontrol_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
miscontrol_event_df.printSchema()

root
 |-- miscontrol: struct (nullable = true)
 |    |-- aerial_won: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- position: str

In [115]:
cols_interest = ['miscontrol.aerial_won'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

miscontrol_event_df_clean = miscontrol_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

miscontrol_event_df_clean.printSchema()

root
 |-- miscontrol_aerial_won: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- duration: double (nullable = true)


### Saving miscontrol event data as parquet

In [116]:
!hdfs dfs -ls Project/Data/Format_data/

Found 36 items
drwxrwxrwx+  - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:52 Project/Data/Format_data/competitions.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:27 Project/Data/Format_data/event_50_50.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-30 23:29 Project/Data/Format_data/event_bad_behaviour.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:58 Project/Data/Format_data/event_ball_receipt.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_ball_recovery.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:00 Project/Data/Format_data/event_block.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_carry.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:01 Project/Data/Format_data/event_clearance.parquet
drwxr-xr-x   

In [117]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_miscontrol.parquet'

In [118]:
!hdfs dfs -rm -R $filename
miscontrol_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_miscontrol.parquet


Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_miscontrol.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      45654 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_miscontrol.parquet/part-00000-9aa938e4-2d46-4c57-a867-ba9d51388fcd-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      52031 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_miscontrol.parquet/part-00001-9aa938e4-2d46-4c57-a867-ba9d51388fcd-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      41740 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_miscontrol.parquet/part-00002-9aa938e4-2d46-4c57-a867-ba9d51388fcd-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      48935 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_miscontrol.parquet/part-00003-9aa938e4-2d46-4c57-a867-ba9d51388fcd-c00

## Foul Won - ID:21

In [119]:
event = 'foul_won'
id_ = event_id_map[event] 
event, id_

('foul_won', 21)

In [120]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
foul_won_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
foul_won_event_df.printSchema()

root
 |-- foul_won: struct (nullable = true)
 |    |-- advantage: boolean (nullable = true)
 |    |-- defensive: boolean (nullable = true)
 |    |-- penalty: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |

In [121]:
cols_interest = ['foul_won.advantage','foul_won.defensive','foul_won.penalty'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

foul_won_event_df_clean = foul_won_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

foul_won_event_df_clean.printSchema()

root
 |-- foul_won_advantage: boolean (nullable = true)
 |-- foul_won_defensive: boolean (nullable = true)
 |-- foul_won_penalty: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable

### Saving foul won event data as parquet

In [122]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_won.parquet'

In [123]:
!hdfs dfs -rm -R $filename
foul_won_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_won.parquet


Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:03 /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_won.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      65786 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_won.parquet/part-00000-f4b6faaf-d502-4d82-952a-f5e0f7f8ed42-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      65477 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_won.parquet/part-00001-f4b6faaf-d502-4d82-952a-f5e0f7f8ed42-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      53105 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_won.parquet/part-00002-f4b6faaf-d502-4d82-952a-f5e0f7f8ed42-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      54570 2023-12-06 21:02 /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_won.parquet/part-00003-f4b6faaf-d502-4d82-952a-f5e0f7f8ed42-c000.snappy.p

## Foul Committed - ID:22

In [15]:
event = 'foul_committed'
id_ = event_id_map[event] 
event, id_

('foul_committed', 22)

In [16]:
event_cols = [col(event),col('counterpress'),*[col(_) for _ in gen_attrs]]
foul_committed_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
foul_committed_event_df.printSchema()

root
 |-- foul_committed: struct (nullable = true)
 |    |-- advantage: boolean (nullable = true)
 |    |-- card: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |-- offensive: boolean (nullable = true)
 |    |-- penalty: boolean (nullable = true)
 |    |-- type: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |-- counterpress: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- nam

In [17]:
cols_interest = ['foul_committed.advantage','foul_committed.card.id','foul_committed.card.name',
                 'foul_committed.offensive','foul_committed.penalty',
                 'foul_committed.type.id','foul_committed.type.name','counterpress'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

foul_committed_event_df_clean = foul_committed_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

foul_committed_event_df_clean.printSchema()

root
 |-- foul_committed_advantage: boolean (nullable = true)
 |-- foul_committed_card_id: long (nullable = true)
 |-- foul_committed_card_name: string (nullable = true)
 |-- foul_committed_offensive: boolean (nullable = true)
 |-- foul_committed_penalty: boolean (nullable = true)
 |-- foul_committed_type_id: long (nullable = true)
 |-- foul_committed_type_name: string (nullable = true)
 |-- counterpress: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = tru

### Saving foul committed event data as parquet

In [18]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_committed.parquet'

In [19]:
!hdfs dfs -rm -R $filename
foul_committed_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_committed.parquet


23/12/09 04:27:22 WARN org.apache.spark.sql.catalyst.util.package: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.


Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-09 04:27 /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_committed.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      71068 2023-12-09 04:27 /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_committed.parquet/part-00000-3cebdb9e-b334-4ee6-bf33-25b997ad729a-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      72078 2023-12-09 04:27 /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_committed.parquet/part-00001-3cebdb9e-b334-4ee6-bf33-25b997ad729a-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      59742 2023-12-09 04:27 /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_committed.parquet/part-00002-3cebdb9e-b334-4ee6-bf33-25b997ad729a-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      61347 2023-12-09 04:27 /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_committed.parquet/part-00003-3cebdb9e-b334-4ee6-b

-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      71395 2023-12-09 04:27 /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_committed.parquet/part-00102-3cebdb9e-b334-4ee6-bf33-25b997ad729a-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      76263 2023-12-09 04:27 /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_committed.parquet/part-00103-3cebdb9e-b334-4ee6-bf33-25b997ad729a-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      72971 2023-12-09 04:27 /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_committed.parquet/part-00104-3cebdb9e-b334-4ee6-bf33-25b997ad729a-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      75280 2023-12-09 04:27 /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_committed.parquet/part-00105-3cebdb9e-b334-4ee6-bf33-25b997ad729a-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      76949 2023-12-09 04:27 /user/dc5415_nyu_edu/Project/Data/Format_data/event_foul_commit

23/12/09 05:14:37 WARN org.apache.spark.deploy.yarn.YarnAllocator: Container from a bad node: container_e02_1691775874963_40418_01_000003 on host: nyu-dataproc-sw-x2f9.c.hpc-dataproc-19b8.internal. Exit status: 143. Diagnostics: [2023-12-09 05:14:36.285]Container killed on request. Exit code is 143
[2023-12-09 05:14:36.287]Container exited with a non-zero exit code 143. 
[2023-12-09 05:14:36.290]Killed by external signal
.
23/12/09 05:14:37 WARN org.apache.spark.scheduler.cluster.YarnSchedulerBackend$YarnSchedulerEndpoint: Requesting driver to remove executor 2 for reason Container from a bad node: container_e02_1691775874963_40418_01_000003 on host: nyu-dataproc-sw-x2f9.c.hpc-dataproc-19b8.internal. Exit status: 143. Diagnostics: [2023-12-09 05:14:36.285]Container killed on request. Exit code is 143
[2023-12-09 05:14:36.287]Container exited with a non-zero exit code 143. 
[2023-12-09 05:14:36.290]Killed by external signal
.
23/12/09 05:14:37 ERROR org.apache.spark.scheduler.cluster.Ya

## Interception - ID:10

In [129]:
event = 'interception'
id_ = event_id_map[event] 
event, id_

('interception', 10)

In [130]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
interception_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
interception_event_df.printSchema()

root
 |-- interception: struct (nullable = true)
 |    |-- outcome: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- 

In [131]:
cols_interest = ['interception.outcome.id','interception.outcome.name'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

interception_event_df_clean = interception_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

interception_event_df_clean.printSchema()

root
 |-- interception_outcome_id: long (nullable = true)
 |-- interception_outcome_name: string (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (conta

### Saving interception event data as parquet

In [132]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_interception.parquet'

In [133]:
!hdfs dfs -rm -R $filename
interception_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_interception.parquet


Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:04 /user/dc5415_nyu_edu/Project/Data/Format_data/event_interception.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      53835 2023-12-06 21:03 /user/dc5415_nyu_edu/Project/Data/Format_data/event_interception.parquet/part-00000-9f41cff6-7615-45cd-8d71-d108e16b0fb9-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      52818 2023-12-06 21:03 /user/dc5415_nyu_edu/Project/Data/Format_data/event_interception.parquet/part-00001-9f41cff6-7615-45cd-8d71-d108e16b0fb9-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      49854 2023-12-06 21:03 /user/dc5415_nyu_edu/Project/Data/Format_data/event_interception.parquet/part-00002-9f41cff6-7615-45cd-8d71-d108e16b0fb9-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      54436 2023-12-06 21:03 /user/dc5415_nyu_edu/Project/Data/Format_data/event_interception.parquet/part-00003-9f41cff6-7615-45cd-8d71-d108e1

-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      54546 2023-12-06 21:03 /user/dc5415_nyu_edu/Project/Data/Format_data/event_interception.parquet/part-00041-9f41cff6-7615-45cd-8d71-d108e16b0fb9-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      52923 2023-12-06 21:03 /user/dc5415_nyu_edu/Project/Data/Format_data/event_interception.parquet/part-00042-9f41cff6-7615-45cd-8d71-d108e16b0fb9-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      55952 2023-12-06 21:03 /user/dc5415_nyu_edu/Project/Data/Format_data/event_interception.parquet/part-00043-9f41cff6-7615-45cd-8d71-d108e16b0fb9-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      57092 2023-12-06 21:03 /user/dc5415_nyu_edu/Project/Data/Format_data/event_interception.parquet/part-00044-9f41cff6-7615-45cd-8d71-d108e16b0fb9-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      64913 2023-12-06 21:03 /user/dc5415_nyu_edu/Project/Data/Format_data/event_interception.parque

## Substitution - ID:19

In [134]:
event = 'substitution'
id_ = event_id_map[event] 
event, id_

('substitution', 19)

In [135]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
substitution_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
substitution_event_df.printSchema()

root
 |-- substitution: struct (nullable = true)
 |    |-- outcome: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |-- replacement: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullabl

In [136]:
cols_interest = ['substitution.outcome.id','substitution.outcome.name','substitution.replacement.id',
                 'substitution.replacement.name'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

substitution_event_df_clean = substitution_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

substitution_event_df_clean.printSchema()

root
 |-- substitution_outcome_id: long (nullable = true)
 |-- substitution_outcome_name: string (nullable = true)
 |-- substitution_replacement_id: long (nullable = true)
 |-- substitution_replacement_name: string (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true

### Saving substitution event data as parquet

In [137]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_substitution.parquet'

In [138]:
!hdfs dfs -rm -R $filename
substitution_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_substitution.parquet


23/12/06 21:04:18 WARN org.apache.spark.deploy.yarn.YarnAllocator: Container from a bad node: container_e02_1691775874963_39387_01_000001 on host: nyu-dataproc-sw-xz5r.c.hpc-dataproc-19b8.internal. Exit status: 143. Diagnostics: [2023-12-06 21:04:17.917]Container killed on request. Exit code is 143
[2023-12-06 21:04:17.917]Container exited with a non-zero exit code 143. 
[2023-12-06 21:04:17.918]Killed by external signal
.
23/12/06 21:04:18 WARN org.apache.spark.scheduler.cluster.YarnSchedulerBackend$YarnSchedulerEndpoint: Requesting driver to remove executor 1 for reason Container from a bad node: container_e02_1691775874963_39387_01_000001 on host: nyu-dataproc-sw-xz5r.c.hpc-dataproc-19b8.internal. Exit status: 143. Diagnostics: [2023-12-06 21:04:17.917]Container killed on request. Exit code is 143
[2023-12-06 21:04:17.917]Container exited with a non-zero exit code 143. 
[2023-12-06 21:04:17.918]Killed by external signal
.
23/12/06 21:04:18 ERROR org.apache.spark.scheduler.cluster.Ya

Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:05 /user/dc5415_nyu_edu/Project/Data/Format_data/event_substitution.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      23898 2023-12-06 21:04 /user/dc5415_nyu_edu/Project/Data/Format_data/event_substitution.parquet/part-00000-378d6265-8157-46b7-b741-a800d396c7b7-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      23607 2023-12-06 21:04 /user/dc5415_nyu_edu/Project/Data/Format_data/event_substitution.parquet/part-00001-378d6265-8157-46b7-b741-a800d396c7b7-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      20264 2023-12-06 21:04 /user/dc5415_nyu_edu/Project/Data/Format_data/event_substitution.parquet/part-00002-378d6265-8157-46b7-b741-a800d396c7b7-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      22770 2023-12-06 21:04 /user/dc5415_nyu_edu/Project/Data/Format_data/event_substitution.parquet/part-00003-378d6265-8157-46b7-b741-a800d3

## Half End - ID:34

In [139]:
event = 'half_end'
id_ = event_id_map[event] 
event, id_

('half_end', 34)

In [140]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
half_end_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
half_end_event_df.printSchema()

root
 |-- half_end: struct (nullable = true)
 |    |-- early_video_end: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- position: 

In [141]:
cols_interest = ['half_end.early_video_end'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

half_end_event_df_clean = half_end_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

half_end_event_df_clean.printSchema()

root
 |-- half_end_early_video_end: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- duration: double (nullable = tru

### Saving half end event data as parquet

In [142]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_half_end.parquet'

In [143]:
!hdfs dfs -rm -R $filename
half_end_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_half_end.parquet


Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:06 /user/dc5415_nyu_edu/Project/Data/Format_data/event_half_end.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      19133 2023-12-06 21:05 /user/dc5415_nyu_edu/Project/Data/Format_data/event_half_end.parquet/part-00000-50d71cdc-3d8b-4f39-aa1e-cebb75482d64-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      18649 2023-12-06 21:05 /user/dc5415_nyu_edu/Project/Data/Format_data/event_half_end.parquet/part-00001-50d71cdc-3d8b-4f39-aa1e-cebb75482d64-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      14552 2023-12-06 21:05 /user/dc5415_nyu_edu/Project/Data/Format_data/event_half_end.parquet/part-00002-50d71cdc-3d8b-4f39-aa1e-cebb75482d64-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      15387 2023-12-06 21:05 /user/dc5415_nyu_edu/Project/Data/Format_data/event_half_end.parquet/part-00003-50d71cdc-3d8b-4f39-aa1e-cebb75482d64-c000.snappy.p

## Half Start - ID:18

In [144]:
event = 'half_start'
id_ = event_id_map[event] 
event, id_

('half_start', 18)

In [145]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
half_start_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
half_start_event_df.printSchema()

root
 |-- half_start: struct (nullable = true)
 |    |-- late_video_start: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- positio

In [146]:
cols_interest = ['half_start.late_video_start'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

half_start_event_df_clean = half_start_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

half_start_event_df_clean.printSchema()

root
 |-- half_start_late_video_start: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- duration: double (nullable = 

### Saving half-start event data as parquet

In [147]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_half_start.parquet'

In [148]:
!hdfs dfs -rm -R $filename
half_start_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_half_start.parquet


Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:07 /user/dc5415_nyu_edu/Project/Data/Format_data/event_half_start.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      18256 2023-12-06 21:06 /user/dc5415_nyu_edu/Project/Data/Format_data/event_half_start.parquet/part-00000-9b295bd7-6bbf-4ab0-859f-bcfaa4607ad8-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      17664 2023-12-06 21:06 /user/dc5415_nyu_edu/Project/Data/Format_data/event_half_start.parquet/part-00001-9b295bd7-6bbf-4ab0-859f-bcfaa4607ad8-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      14156 2023-12-06 21:06 /user/dc5415_nyu_edu/Project/Data/Format_data/event_half_start.parquet/part-00002-9b295bd7-6bbf-4ab0-859f-bcfaa4607ad8-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      14750 2023-12-06 21:06 /user/dc5415_nyu_edu/Project/Data/Format_data/event_half_start.parquet/part-00003-9b295bd7-6bbf-4ab0-859f-bcfaa4607ad8-c00

## Injury Stoppage - ID:40

In [149]:
event = 'injury_stoppage'
id_ = event_id_map[event] 
event, id_

('injury_stoppage', 40)

In [150]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
injury_stoppage_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
injury_stoppage_event_df.printSchema()

root
 |-- injury_stoppage: struct (nullable = true)
 |    |-- in_chain: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- position: 

In [151]:
cols_interest = ['injury_stoppage.in_chain'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

injury_stoppage_event_df_clean = injury_stoppage_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

injury_stoppage_event_df_clean.printSchema()

root
 |-- injury_stoppage_in_chain: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- duration: double (nullable = tru

### Saving injury stoppage event data as parquet

In [152]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_injury_stoppage.parquet'

In [153]:
!hdfs dfs -rm -R $filename
injury_stoppage_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_injury_stoppage.parquet


Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:08 /user/dc5415_nyu_edu/Project/Data/Format_data/event_injury_stoppage.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      14452 2023-12-06 21:07 /user/dc5415_nyu_edu/Project/Data/Format_data/event_injury_stoppage.parquet/part-00000-9a9dfd5a-5824-4db6-801c-548a0ed4b353-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      16553 2023-12-06 21:07 /user/dc5415_nyu_edu/Project/Data/Format_data/event_injury_stoppage.parquet/part-00001-9a9dfd5a-5824-4db6-801c-548a0ed4b353-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      13389 2023-12-06 21:07 /user/dc5415_nyu_edu/Project/Data/Format_data/event_injury_stoppage.parquet/part-00002-9a9dfd5a-5824-4db6-801c-548a0ed4b353-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      11684 2023-12-06 21:07 /user/dc5415_nyu_edu/Project/Data/Format_data/event_injury_stoppage.parquet/part-00003-9a9dfd5a-5824-4

## 50/50 - ID:33

In [154]:
event = '50_50'
id_ = event_id_map[event] 
event, id_

('50_50', 33)

In [155]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
f_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
f_event_df.printSchema()

root
 |-- 50_50: struct (nullable = true)
 |    |-- outcome: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id: lon

In [156]:
cols_interest = ['50_50.outcome.id','50_50.outcome.name'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

f_event_df_clean = f_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

f_event_df_clean.printSchema()

root
 |-- 50_50_outcome_id: long (nullable = true)
 |-- 50_50_outcome_name: string (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsNull = true

### Saving 50/50 event data as parquet

In [157]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_50_50.parquet'

In [158]:
!hdfs dfs -rm -R $filename
f_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_50_50.parquet


Found 206 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:09 /user/dc5415_nyu_edu/Project/Data/Format_data/event_50_50.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      13392 2023-12-06 21:08 /user/dc5415_nyu_edu/Project/Data/Format_data/event_50_50.parquet/part-00000-e43d8486-b3c3-4c32-8c98-62028ff36a8b-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      14701 2023-12-06 21:08 /user/dc5415_nyu_edu/Project/Data/Format_data/event_50_50.parquet/part-00001-e43d8486-b3c3-4c32-8c98-62028ff36a8b-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      14066 2023-12-06 21:08 /user/dc5415_nyu_edu/Project/Data/Format_data/event_50_50.parquet/part-00002-e43d8486-b3c3-4c32-8c98-62028ff36a8b-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      18834 2023-12-06 21:08 /user/dc5415_nyu_edu/Project/Data/Format_data/event_50_50.parquet/part-00003-e43d8486-b3c3-4c32-8c98-62028ff36a8b-c000.snappy.parquet
-rw-r--r

## Tactical Shift - ID:36

In [159]:
event = 'tactics'
id_ = event_id_map[event] 
event, id_

('tactics', 36)

In [160]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
tactical_shift_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
tactical_shift_event_df.printSchema()

root
 |-- tactics: struct (nullable = true)
 |    |-- formation: long (nullable = true)
 |    |-- lineup: array (nullable = true)
 |    |    |-- element: struct (containsNull = true)
 |    |    |    |-- jersey_number: long (nullable = true)
 |    |    |    |-- player: struct (nullable = true)
 |    |    |    |    |-- id: long (nullable = true)
 |    |    |    |    |-- name: string (nullable = true)
 |    |    |    |-- position: struct (nullable = true)
 |    |    |    |    |-- id: long (nullable = true)
 |    |    |    |    |-- name: string (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: str

In [161]:
cols_interest = ['tactics.formation','tactics.lineup.jersey_number',
                 'tactics.lineup.player.id','tactics.lineup.player.name',
                'tactics.lineup.position.id','tactics.lineup.position.name'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

tactical_shift_event_df_clean = tactical_shift_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

tactical_shift_event_df_clean.printSchema()

root
 |-- tactics_formation: long (nullable = true)
 |-- tactics_lineup_jersey_number: array (nullable = true)
 |    |-- element: long (containsNull = true)
 |-- tactics_lineup_player_id: array (nullable = true)
 |    |-- element: long (containsNull = true)
 |-- tactics_lineup_player_name: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- tactics_lineup_position_id: array (nullable = true)
 |    |-- element: long (containsNull = true)
 |-- tactics_lineup_position_name: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- 

### Saving tactical shift event data as parquet

In [162]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_tactics.parquet'

In [163]:
!hdfs dfs -rm -R $filename
tactical_shift_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_tactics.parquet


Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:09 /user/dc5415_nyu_edu/Project/Data/Format_data/event_tactics.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      21606 2023-12-06 21:09 /user/dc5415_nyu_edu/Project/Data/Format_data/event_tactics.parquet/part-00000-b1f210b7-1760-4689-8c1c-b2c95c541544-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      22191 2023-12-06 21:09 /user/dc5415_nyu_edu/Project/Data/Format_data/event_tactics.parquet/part-00001-b1f210b7-1760-4689-8c1c-b2c95c541544-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      18689 2023-12-06 21:09 /user/dc5415_nyu_edu/Project/Data/Format_data/event_tactics.parquet/part-00002-b1f210b7-1760-4689-8c1c-b2c95c541544-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      21815 2023-12-06 21:09 /user/dc5415_nyu_edu/Project/Data/Format_data/event_tactics.parquet/part-00003-b1f210b7-1760-4689-8c1c-b2c95c541544-c000.snappy.parque

## Player Off - ID:27

In [164]:
event = 'player_off'
id_ = event_id_map[event] 
event, id_

('player_off', 27)

In [165]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
player_off_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
player_off_event_df.printSchema()

root
 |-- player_off: struct (nullable = true)
 |    |-- permanent: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- position: stru

In [166]:
cols_interest = ['player_off.permanent'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

player_off_event_df_clean = player_off_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

player_off_event_df_clean.printSchema()

root
 |-- player_off_permanent: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- duration: double (nullable = true)
 

### Saving player off event data as parquet

In [167]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_player_off.parquet'

In [168]:
!hdfs dfs -rm -R $filename
player_off_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_off.parquet


Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:10 /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_off.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       9433 2023-12-06 21:10 /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_off.parquet/part-00000-18cff3d8-8086-421a-b8e9-017d6217587d-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       9707 2023-12-06 21:10 /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_off.parquet/part-00001-18cff3d8-8086-421a-b8e9-017d6217587d-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       9767 2023-12-06 21:10 /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_off.parquet/part-00002-18cff3d8-8086-421a-b8e9-017d6217587d-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8894 2023-12-06 21:10 /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_off.parquet/part-00003-18cff3d8-8086-421a-b8e9-017d6217587d-c00

## Bad Behaviour - ID:24

In [169]:
event = 'bad_behaviour'
id_ = event_id_map[event] 
event, id_

('bad_behaviour', 24)

In [170]:
event_cols = [col(event),*[col(_) for _ in gen_attrs]]
bad_behaviour_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
bad_behaviour_event_df.printSchema()

root
 |-- bad_behaviour: struct (nullable = true)
 |    |-- card: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id

In [171]:
cols_interest = ['bad_behaviour.card.id','bad_behaviour.card.name'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

bad_behaviour_event_df_clean = bad_behaviour_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

bad_behaviour_event_df_clean.printSchema()

root
 |-- bad_behaviour_card_id: long (nullable = true)
 |-- bad_behaviour_card_name: string (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsN

### Saving bad behavior event data as parquet

In [172]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_bad_behaviour.parquet'

In [173]:
!hdfs dfs -rm -R $filename
bad_behaviour_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_bad_behaviour.parquet


Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:11 /user/dc5415_nyu_edu/Project/Data/Format_data/event_bad_behaviour.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       9984 2023-12-06 21:10 /user/dc5415_nyu_edu/Project/Data/Format_data/event_bad_behaviour.parquet/part-00000-a8e0fe27-d367-4e99-a47f-6c12b280d14f-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      10478 2023-12-06 21:10 /user/dc5415_nyu_edu/Project/Data/Format_data/event_bad_behaviour.parquet/part-00001-a8e0fe27-d367-4e99-a47f-6c12b280d14f-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      10001 2023-12-06 21:10 /user/dc5415_nyu_edu/Project/Data/Format_data/event_bad_behaviour.parquet/part-00002-a8e0fe27-d367-4e99-a47f-6c12b280d14f-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       9303 2023-12-06 21:10 /user/dc5415_nyu_edu/Project/Data/Format_data/event_bad_behaviour.parquet/part-00003-a8e0fe27-d367-4e99-a47f-6

## Error - ID:37

In [174]:
event = 'error'
id_ = event_id_map[event] 
event, id_

('error', 37)

In [175]:
event_cols = [*[col(_) for _ in gen_attrs]]
error_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
error_event_df = error_event_df.withColumn(event,lit(1))
error_event_df.printSchema()

root
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- position: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullabl

In [176]:
cols_interest = [event] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

error_event_df_clean = error_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

error_event_df_clean.printSchema()

root
 |-- error: integer (nullable = false)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- duration: double (nullable = true)
 |-- under_pres

### Saving error event data as parquet

In [177]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_error.parquet'

In [ ]:
!hdfs dfs -rm -R $filename
error_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_error.parquet


## Offside - ID:8

In [ ]:
event = 'offside'
id_ = event_id_map[event] 
event, id_

In [ ]:
event_cols = [*[col(_) for _ in gen_attrs]]
offside_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
offside_event_df = offside_event_df.withColumn(event,lit(1))
offside_event_df.printSchema()

In [ ]:
cols_interest = [event] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

offside_event_df_clean = offside_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

offside_event_df_clean.printSchema()

### Saving offside event data as parquet

In [ ]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

In [ ]:
!hdfs dfs -rm -R $filename
offside_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

## Referee Ball-Drop - ID:41

In [ ]:
event = 'ref_ball_drop'
id_ = event_id_map[event] 
event, id_

In [ ]:
event_cols = [*[col(_) for _ in gen_attrs]]
ref_ball_drop_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
ref_ball_drop_event_df = ref_ball_drop_event_df.withColumn(event,lit(1))
ref_ball_drop_event_df.printSchema()

In [ ]:
cols_interest = [event] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

ref_ball_drop_event_df_clean = ref_ball_drop_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

ref_ball_drop_event_df_clean.printSchema()

### Saving Refree ball-drop event data as parquet

In [ ]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

In [188]:
!hdfs dfs -rm -R $filename
ref_ball_drop_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:14 /user/dc5415_nyu_edu/Project/Data/Format_data/event_ref_ball_drop.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       9659 2023-12-06 21:13 /user/dc5415_nyu_edu/Project/Data/Format_data/event_ref_ball_drop.parquet/part-00000-0fb2e85e-95b3-4c62-8f1c-aecaaa58d765-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      11548 2023-12-06 21:13 /user/dc5415_nyu_edu/Project/Data/Format_data/event_ref_ball_drop.parquet/part-00001-0fb2e85e-95b3-4c62-8f1c-aecaaa58d765-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      10288 2023-12-06 21:13 /user/dc5415_nyu_edu/Project/Data/Format_data/event_ref_ball_drop.parquet/part-00002-0fb2e85e-95b3-4c62-8f1c-aecaaa58d765-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8458 2023-12-06 21:13 /user/dc5415_nyu_edu/Project/Data/Format_data/event_ref_ball_drop.parquet/part-00003-0fb2e85e-95b3-4c62-8f1c-a

-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       9540 2023-12-06 21:13 /user/dc5415_nyu_edu/Project/Data/Format_data/event_ref_ball_drop.parquet/part-00077-0fb2e85e-95b3-4c62-8f1c-aecaaa58d765-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       9262 2023-12-06 21:13 /user/dc5415_nyu_edu/Project/Data/Format_data/event_ref_ball_drop.parquet/part-00078-0fb2e85e-95b3-4c62-8f1c-aecaaa58d765-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       9324 2023-12-06 21:13 /user/dc5415_nyu_edu/Project/Data/Format_data/event_ref_ball_drop.parquet/part-00079-0fb2e85e-95b3-4c62-8f1c-aecaaa58d765-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8772 2023-12-06 21:13 /user/dc5415_nyu_edu/Project/Data/Format_data/event_ref_ball_drop.parquet/part-00080-0fb2e85e-95b3-4c62-8f1c-aecaaa58d765-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8641 2023-12-06 21:13 /user/dc5415_nyu_edu/Project/Data/Format_data/event_ref_ball_drop.p

## Own Goal Against - ID:20

In [189]:
event = 'og_agnst'
id_ = event_id_map[event] 
event, id_

('og_agnst', 20)

In [190]:
event_cols = [*[col(_) for _ in gen_attrs]]
og_agnst_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
og_agnst_event_df = og_agnst_event_df.withColumn(event,lit(1))
og_agnst_event_df.printSchema()

root
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- position: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullabl

In [191]:
cols_interest = [event] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

og_agnst_event_df_clean = og_agnst_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

og_agnst_event_df_clean.printSchema()

root
 |-- og_agnst: integer (nullable = false)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- duration: double (nullable = true)
 |-- under_p

### Saving Own Goal Against event data as parquet

In [192]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_og_agnst.parquet'

In [193]:
!hdfs dfs -rm -R $filename
og_agnst_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_agnst.parquet


Found 165 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:14 /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_agnst.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8899 2023-12-06 21:14 /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_agnst.parquet/part-00000-e1ebb0d4-1936-4e79-9fb2-16a5977025b4-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8377 2023-12-06 21:14 /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_agnst.parquet/part-00001-e1ebb0d4-1936-4e79-9fb2-16a5977025b4-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8389 2023-12-06 21:14 /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_agnst.parquet/part-00003-e1ebb0d4-1936-4e79-9fb2-16a5977025b4-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8690 2023-12-06 21:14 /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_agnst.parquet/part-00004-e1ebb0d4-1936-4e79-9fb2-16a5977025b4-c000.snappy.p

-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8150 2023-12-06 21:14 /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_agnst.parquet/part-00150-e1ebb0d4-1936-4e79-9fb2-16a5977025b4-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8354 2023-12-06 21:14 /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_agnst.parquet/part-00151-e1ebb0d4-1936-4e79-9fb2-16a5977025b4-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8325 2023-12-06 21:14 /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_agnst.parquet/part-00154-e1ebb0d4-1936-4e79-9fb2-16a5977025b4-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8204 2023-12-06 21:14 /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_agnst.parquet/part-00155-e1ebb0d4-1936-4e79-9fb2-16a5977025b4-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8639 2023-12-06 21:14 /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_agnst.parquet/part-00156-e1ebb0d

## Own Goal For - ID:25

In [194]:
event = 'og_for'
id_ = event_id_map[event] 
event, id_

('og_for', 25)

In [195]:
event_cols = [*[col(_) for _ in gen_attrs]]
og_for_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
og_for_event_df = og_for_event_df.withColumn(event,lit(1))
og_for_event_df.printSchema()

root
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- position: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullabl

In [196]:
cols_interest = [event] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

og_for_event_df_clean = og_for_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

og_for_event_df_clean.printSchema()

root
 |-- og_for: integer (nullable = false)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- duration: double (nullable = true)
 |-- under_pre

### Saving Own Goal For event data as parquet

In [197]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_og_for.parquet'

In [198]:
!hdfs dfs -rm -R $filename
og_for_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_for.parquet


Found 165 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:15 /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_for.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8349 2023-12-06 21:15 /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_for.parquet/part-00000-43a330c4-996b-4582-ae51-4006b1549cc5-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8396 2023-12-06 21:15 /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_for.parquet/part-00001-43a330c4-996b-4582-ae51-4006b1549cc5-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       7859 2023-12-06 21:15 /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_for.parquet/part-00003-43a330c4-996b-4582-ae51-4006b1549cc5-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8751 2023-12-06 21:15 /user/dc5415_nyu_edu/Project/Data/Format_data/event_og_for.parquet/part-00004-43a330c4-996b-4582-ae51-4006b1549cc5-c000.snappy.parquet
-rw

## Dispossesed - ID:3

In [199]:
event = 'dispossesed'
id_ = event_id_map[event] 
event, id_

('dispossesed', 3)

In [200]:
event_cols = [*[col(_) for _ in gen_attrs]]
dispossed_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
dispossed_event_df = dispossed_event_df.withColumn(event,lit(1))
dispossed_event_df.printSchema()

root
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- position: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullabl

In [201]:
cols_interest = [event] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

dispossed_event_df_clean = dispossed_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

dispossed_event_df_clean.printSchema()

root
 |-- dispossesed: integer (nullable = false)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- duration: double (nullable = true)
 |-- unde

### Saving dispossed event data as parquet

In [202]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_dispossesed.parquet'

In [203]:
!hdfs dfs -rm -R $filename
dispossed_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_dispossesed.parquet


Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:16 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dispossesed.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      55807 2023-12-06 21:15 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dispossesed.parquet/part-00000-03fd31dd-3a90-4e4c-99d9-9bc9c3587358-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      58152 2023-12-06 21:15 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dispossesed.parquet/part-00001-03fd31dd-3a90-4e4c-99d9-9bc9c3587358-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      51628 2023-12-06 21:16 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dispossesed.parquet/part-00002-03fd31dd-3a90-4e4c-99d9-9bc9c3587358-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      51972 2023-12-06 21:15 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dispossesed.parquet/part-00003-03fd31dd-3a90-4e4c-99d9-9bc9c358735

## Starting XI - ID:35

In [204]:
event = 'start_xi'
id_ = event_id_map[event] 
event, id_

('start_xi', 35)

In [205]:
event_cols = [col(event),col('tactics'),*[col(_) for _ in gen_attrs]]
event_df = event_df.withColumn(event,lit(1))
start_xi_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
start_xi_event_df.printSchema()

root
 |-- start_xi: integer (nullable = false)
 |-- tactics: struct (nullable = true)
 |    |-- formation: long (nullable = true)
 |    |-- lineup: array (nullable = true)
 |    |    |-- element: struct (containsNull = true)
 |    |    |    |-- jersey_number: long (nullable = true)
 |    |    |    |-- player: struct (nullable = true)
 |    |    |    |    |-- id: long (nullable = true)
 |    |    |    |    |-- name: string (nullable = true)
 |    |    |    |-- position: struct (nullable = true)
 |    |    |    |    |-- id: long (nullable = true)
 |    |    |    |    |-- name: string (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (

In [206]:
cols_interest = ['start_xi','tactics.formation','tactics.lineup.jersey_number',
                 'tactics.lineup.player.id','tactics.lineup.player.name',
                'tactics.lineup.position.id','tactics.lineup.position.name'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

start_xi_event_df_clean = start_xi_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])
start_xi_event_df_clean.printSchema()

root
 |-- start_xi: integer (nullable = false)
 |-- tactics_formation: long (nullable = true)
 |-- tactics_lineup_jersey_number: array (nullable = true)
 |    |-- element: long (containsNull = true)
 |-- tactics_lineup_player_id: array (nullable = true)
 |    |-- element: long (containsNull = true)
 |-- tactics_lineup_player_name: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- tactics_lineup_position_id: array (nullable = true)
 |    |-- element: long (containsNull = true)
 |-- tactics_lineup_position_name: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- posses

### Saving start_xi event data as parquet

In [207]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_start_xi.parquet'

In [208]:
!hdfs dfs -rm -R $filename
start_xi_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_start_xi.parquet


Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_start_xi.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      19191 2023-12-06 21:16 /user/dc5415_nyu_edu/Project/Data/Format_data/event_start_xi.parquet/part-00000-e3f3fcd1-83f8-47cb-aa09-bb5393eb43a1-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      19497 2023-12-06 21:16 /user/dc5415_nyu_edu/Project/Data/Format_data/event_start_xi.parquet/part-00001-e3f3fcd1-83f8-47cb-aa09-bb5393eb43a1-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      19378 2023-12-06 21:16 /user/dc5415_nyu_edu/Project/Data/Format_data/event_start_xi.parquet/part-00002-e3f3fcd1-83f8-47cb-aa09-bb5393eb43a1-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      20160 2023-12-06 21:16 /user/dc5415_nyu_edu/Project/Data/Format_data/event_start_xi.parquet/part-00003-e3f3fcd1-83f8-47cb-aa09-bb5393eb43a1-c000.snappy.p

-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      21742 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_start_xi.parquet/part-00114-e3f3fcd1-83f8-47cb-aa09-bb5393eb43a1-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      21985 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_start_xi.parquet/part-00115-e3f3fcd1-83f8-47cb-aa09-bb5393eb43a1-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      21739 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_start_xi.parquet/part-00116-e3f3fcd1-83f8-47cb-aa09-bb5393eb43a1-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      21654 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_start_xi.parquet/part-00117-e3f3fcd1-83f8-47cb-aa09-bb5393eb43a1-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      21875 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_start_xi.parquet/part-00118-e3f3fcd

## Player on - ID:26

In [209]:
event = 'player_on'
id_ = event_id_map[event] 
event, id_

('player_on', 26)

In [210]:
event_cols = [*[col(_) for _ in gen_attrs]]
play_on_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
play_on_event_df = play_on_event_df.withColumn(event,lit(1))
play_on_event_df.printSchema()

root
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- position: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullabl

In [211]:
cols_interest = [event] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

play_on_event_df_clean = play_on_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

play_on_event_df_clean.printSchema()

root
 |-- player_on: integer (nullable = false)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- duration: double (nullable = true)
 |-- under_

### Saving play_on event data as parquet

In [212]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_player_on.parquet'

In [213]:
!hdfs dfs -rm -R $filename
play_on_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_on.parquet


Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_on.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       9530 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_on.parquet/part-00000-ff3a010e-6c0d-4650-b6cd-a3b35660d7a9-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       9643 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_on.parquet/part-00001-ff3a010e-6c0d-4650-b6cd-a3b35660d7a9-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       9744 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_on.parquet/part-00002-ff3a010e-6c0d-4650-b6cd-a3b35660d7a9-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       8932 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_on.parquet/part-00003-ff3a010e-6c0d-4650-b6cd-a3b35660d7a9-c000.sna

-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      10583 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_on.parquet/part-00145-ff3a010e-6c0d-4650-b6cd-a3b35660d7a9-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      11197 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_on.parquet/part-00146-ff3a010e-6c0d-4650-b6cd-a3b35660d7a9-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      12274 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_on.parquet/part-00147-ff3a010e-6c0d-4650-b6cd-a3b35660d7a9-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu       9989 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_on.parquet/part-00148-ff3a010e-6c0d-4650-b6cd-a3b35660d7a9-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      11547 2023-12-06 21:17 /user/dc5415_nyu_edu/Project/Data/Format_data/event_player_on.parquet/part-00149-ff

## Shield - ID:28

In [214]:
event = 'shield'
id_ = event_id_map[event] 
event, id_

('shield', 28)

In [215]:
event_cols = [*[col(_) for _ in gen_attrs]]
shield_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
shield_event_df = shield_event_df.withColumn(event,lit(1))
shield_event_df.printSchema()

root
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- position: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullabl

In [216]:
cols_interest = [event] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

shield_event_df_clean = shield_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

shield_event_df_clean.printSchema()

root
 |-- shield: integer (nullable = false)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-- duration: double (nullable = true)
 |-- under_pre

### Saving shield event data as parquet

In [217]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_shield.parquet'

In [218]:
!hdfs dfs -rm -R $filename
shield_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_shield.parquet


Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:18 /user/dc5415_nyu_edu/Project/Data/Format_data/event_shield.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      11414 2023-12-06 21:18 /user/dc5415_nyu_edu/Project/Data/Format_data/event_shield.parquet/part-00000-51bab9ae-5d2d-474d-b106-b79608783a69-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      11092 2023-12-06 21:18 /user/dc5415_nyu_edu/Project/Data/Format_data/event_shield.parquet/part-00001-51bab9ae-5d2d-474d-b106-b79608783a69-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      10778 2023-12-06 21:18 /user/dc5415_nyu_edu/Project/Data/Format_data/event_shield.parquet/part-00002-51bab9ae-5d2d-474d-b106-b79608783a69-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      10916 2023-12-06 21:18 /user/dc5415_nyu_edu/Project/Data/Format_data/event_shield.parquet/part-00003-51bab9ae-5d2d-474d-b106-b79608783a69-c000.snappy.parquet
-rw

## Dribbled Past - ID:39

In [219]:
event = 'dribble_past'
id_ = event_id_map[event] 
event, id_

('dribble_past', 39)

In [220]:
event_cols = ['counterpress',*[col(_) for _ in gen_attrs]]
dribble_past_event_df = event_df.filter(col('type.id')==id_).select(event_cols)
dribble_past_event_df = dribble_past_event_df.withColumn(event,lit(1))
dribble_past_event_df.printSchema()

root
 |-- counterpress: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- play_pattern: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- team: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- player: struct (nullable = true)
 |    |-- id: long (nullable = true)
 |    |-- name: string (nullable = true)
 |-- position: struct (nullable = true)
 |    |-- id: long (nul

In [221]:
cols_interest = [event,'counterpress'] + gen_attr_schema

alias = [_.replace('.','_') for _ in cols_interest]

dribble_past_event_df_clean = dribble_past_event_df.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

dribble_past_event_df_clean.printSchema()

root
 |-- dribble_past: integer (nullable = false)
 |-- counterpress: boolean (nullable = true)
 |-- match_id: long (nullable = true)
 |-- id: string (nullable = true)
 |-- index: long (nullable = true)
 |-- period: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- minute: long (nullable = true)
 |-- second: long (nullable = true)
 |-- type_id: long (nullable = true)
 |-- type_name: string (nullable = true)
 |-- possession: long (nullable = true)
 |-- possession_team_id: long (nullable = true)
 |-- possession_team_name: string (nullable = true)
 |-- play_pattern_id: long (nullable = true)
 |-- play_pattern_name: string (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- player_id: long (nullable = true)
 |-- player_name: string (nullable = true)
 |-- position_id: long (nullable = true)
 |-- position_name: string (nullable = true)
 |-- location: array (nullable = true)
 |    |-- element: double (containsNull = true)
 |-

### Saving dribble_past event data as parquet

In [222]:
filename = f"{new_data_dir}event_{event}.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble_past.parquet'

In [223]:
!hdfs dfs -rm -R $filename
dribble_past_event_df_clean.write.parquet(filename)
!hdfs dfs -ls $filename

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble_past.parquet


Found 207 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:18 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble_past.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      75414 2023-12-06 21:18 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble_past.parquet/part-00000-ea498a39-fdb6-4aa7-bd27-172120c707c4-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      68128 2023-12-06 21:18 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble_past.parquet/part-00001-ea498a39-fdb6-4aa7-bd27-172120c707c4-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      67016 2023-12-06 21:18 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble_past.parquet/part-00002-ea498a39-fdb6-4aa7-bd27-172120c707c4-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      65323 2023-12-06 21:18 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble_past.parquet/part-00003-ea498a39-fdb6-4aa7-bd27-172120

-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      62393 2023-12-06 21:18 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble_past.parquet/part-00091-ea498a39-fdb6-4aa7-bd27-172120c707c4-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      81151 2023-12-06 21:18 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble_past.parquet/part-00092-ea498a39-fdb6-4aa7-bd27-172120c707c4-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      78712 2023-12-06 21:18 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble_past.parquet/part-00093-ea498a39-fdb6-4aa7-bd27-172120c707c4-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      73242 2023-12-06 21:18 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble_past.parquet/part-00094-ea498a39-fdb6-4aa7-bd27-172120c707c4-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      76086 2023-12-06 21:18 /user/dc5415_nyu_edu/Project/Data/Format_data/event_dribble_past.parque

# Lineups data

In [229]:
file_path = "Project/Data/data/lineups_/*.json"

In [230]:
lineup_df = spark.read.option("multiline","true").json(file_path)

In [231]:
lineup_df.count()

6398

In [232]:
lineup_df.printSchema()

root
 |-- lineup: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- cards: array (nullable = true)
 |    |    |    |-- element: struct (containsNull = true)
 |    |    |    |    |-- card_type: string (nullable = true)
 |    |    |    |    |-- period: long (nullable = true)
 |    |    |    |    |-- reason: string (nullable = true)
 |    |    |    |    |-- time: string (nullable = true)
 |    |    |-- country: struct (nullable = true)
 |    |    |    |-- id: long (nullable = true)
 |    |    |    |-- name: string (nullable = true)
 |    |    |-- jersey_number: long (nullable = true)
 |    |    |-- player_id: long (nullable = true)
 |    |    |-- player_name: string (nullable = true)
 |    |    |-- player_nickname: string (nullable = true)
 |    |    |-- positions: array (nullable = true)
 |    |    |    |-- element: struct (containsNull = true)
 |    |    |    |    |-- end_reason: string (nullable = true)
 |    |    |    |    |-- from: string (nullabl

In [233]:
cols_interest = ['match_id','team_id','team_name','lineup']


lineup_df_clean = lineup_df.select(*[col(_) if _ != 'lineup'  else col(_)[0].alias(_) for _ in cols_interest])

In [234]:
lineup_df_clean.printSchema()

root
 |-- match_id: long (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- lineup: struct (nullable = true)
 |    |-- cards: array (nullable = true)
 |    |    |-- element: struct (containsNull = true)
 |    |    |    |-- card_type: string (nullable = true)
 |    |    |    |-- period: long (nullable = true)
 |    |    |    |-- reason: string (nullable = true)
 |    |    |    |-- time: string (nullable = true)
 |    |-- country: struct (nullable = true)
 |    |    |-- id: long (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |-- jersey_number: long (nullable = true)
 |    |-- player_id: long (nullable = true)
 |    |-- player_name: string (nullable = true)
 |    |-- player_nickname: string (nullable = true)
 |    |-- positions: array (nullable = true)
 |    |    |-- element: struct (containsNull = true)
 |    |    |    |-- end_reason: string (nullable = true)
 |    |    |    |-- from: string (nullable = true)
 |    

In [235]:
cols_interest = ['match_id','team_id','team_name','lineup.cards','lineup.country.id','lineup.country.name',
                 'lineup.jersey_number','lineup.player_id','lineup.player_name','lineup.player_nickname',
                 'lineup.positions']

alias = [_.replace('.','_') for _ in cols_interest]

lineup_df_clean = lineup_df_clean.select(*[col(n)[0].alias(a) if (('positions' in n) or ('cards' in n)) else col(n).alias(a)
                           for n,a in zip(cols_interest,alias)])

In [236]:
lineup_df_clean.printSchema()

root
 |-- match_id: long (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- lineup_cards: struct (nullable = true)
 |    |-- card_type: string (nullable = true)
 |    |-- period: long (nullable = true)
 |    |-- reason: string (nullable = true)
 |    |-- time: string (nullable = true)
 |-- lineup_country_id: long (nullable = true)
 |-- lineup_country_name: string (nullable = true)
 |-- lineup_jersey_number: long (nullable = true)
 |-- lineup_player_id: long (nullable = true)
 |-- lineup_player_name: string (nullable = true)
 |-- lineup_player_nickname: string (nullable = true)
 |-- lineup_positions: struct (nullable = true)
 |    |-- end_reason: string (nullable = true)
 |    |-- from: string (nullable = true)
 |    |-- from_period: long (nullable = true)
 |    |-- position: string (nullable = true)
 |    |-- position_id: long (nullable = true)
 |    |-- start_reason: string (nullable = true)
 |    |-- to: string (nullable = true)
 |   

In [237]:
cols_interest = ['match_id','team_id','team_name','lineup_cards.card_type','lineup_cards.period','lineup_cards.reason',
                 'lineup_cards.time','lineup_country_id','lineup_country_name','lineup_jersey_number',
                 'lineup_player_id','lineup_player_name','lineup_player_nickname','lineup_positions.end_reason',
                'lineup_positions.from','lineup_positions.from_period','lineup_positions.position',
                 'lineup_positions.position_id','lineup_positions.start_reason','lineup_positions.to',
                 'lineup_positions.to_period']

alias = [_.replace('.','_') for _ in cols_interest]

lineup_df_clean = lineup_df_clean.select(*[col(n).alias(a) for n,a in zip(cols_interest,alias)])

In [238]:
lineup_df_clean.printSchema()

root
 |-- match_id: long (nullable = true)
 |-- team_id: long (nullable = true)
 |-- team_name: string (nullable = true)
 |-- lineup_cards_card_type: string (nullable = true)
 |-- lineup_cards_period: long (nullable = true)
 |-- lineup_cards_reason: string (nullable = true)
 |-- lineup_cards_time: string (nullable = true)
 |-- lineup_country_id: long (nullable = true)
 |-- lineup_country_name: string (nullable = true)
 |-- lineup_jersey_number: long (nullable = true)
 |-- lineup_player_id: long (nullable = true)
 |-- lineup_player_name: string (nullable = true)
 |-- lineup_player_nickname: string (nullable = true)
 |-- lineup_positions_end_reason: string (nullable = true)
 |-- lineup_positions_from: string (nullable = true)
 |-- lineup_positions_from_period: long (nullable = true)
 |-- lineup_positions_position: string (nullable = true)
 |-- lineup_positions_position_id: long (nullable = true)
 |-- lineup_positions_start_reason: string (nullable = true)
 |-- lineup_positions_to: string

## Saving lineup data as parquet

In [239]:
!hdfs dfs -ls Project/Data/Format_data/

Found 36 items
drwxrwxrwx+  - dc5415_nyu_edu dc5415_nyu_edu          0 2023-11-14 22:52 Project/Data/Format_data/competitions.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:09 Project/Data/Format_data/event_50_50.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:11 Project/Data/Format_data/event_bad_behaviour.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:58 Project/Data/Format_data/event_ball_receipt.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_ball_recovery.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:00 Project/Data/Format_data/event_block.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 20:59 Project/Data/Format_data/event_carry.parquet
drwxr-xr-x   - dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:01 Project/Data/Format_data/event_clearance.parquet
drwxr-xr-x   

In [240]:
filename = f"{new_data_dir}lineups.parquet"
filename

'/user/dc5415_nyu_edu/Project/Data/Format_data/lineups.parquet'

In [241]:
!hdfs dfs -rm -R $filename
lineup_df_clean.write.parquet(filename)

Deleted /user/dc5415_nyu_edu/Project/Data/Format_data/lineups.parquet


In [242]:
!hdfs dfs -ls $filename

Found 101 items
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu          0 2023-12-06 21:43 /user/dc5415_nyu_edu/Project/Data/Format_data/lineups.parquet/_SUCCESS
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      11706 2023-12-06 21:43 /user/dc5415_nyu_edu/Project/Data/Format_data/lineups.parquet/part-00000-eb7d7c50-6c24-4e0d-9ec0-242782ea7493-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      11929 2023-12-06 21:43 /user/dc5415_nyu_edu/Project/Data/Format_data/lineups.parquet/part-00001-eb7d7c50-6c24-4e0d-9ec0-242782ea7493-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      11869 2023-12-06 21:43 /user/dc5415_nyu_edu/Project/Data/Format_data/lineups.parquet/part-00002-eb7d7c50-6c24-4e0d-9ec0-242782ea7493-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      11385 2023-12-06 21:43 /user/dc5415_nyu_edu/Project/Data/Format_data/lineups.parquet/part-00003-eb7d7c50-6c24-4e0d-9ec0-242782ea7493-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_ed

-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      11600 2023-12-06 21:43 /user/dc5415_nyu_edu/Project/Data/Format_data/lineups.parquet/part-00086-eb7d7c50-6c24-4e0d-9ec0-242782ea7493-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      11459 2023-12-06 21:43 /user/dc5415_nyu_edu/Project/Data/Format_data/lineups.parquet/part-00087-eb7d7c50-6c24-4e0d-9ec0-242782ea7493-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      11606 2023-12-06 21:43 /user/dc5415_nyu_edu/Project/Data/Format_data/lineups.parquet/part-00088-eb7d7c50-6c24-4e0d-9ec0-242782ea7493-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      11495 2023-12-06 21:43 /user/dc5415_nyu_edu/Project/Data/Format_data/lineups.parquet/part-00089-eb7d7c50-6c24-4e0d-9ec0-242782ea7493-c000.snappy.parquet
-rw-r--r--   1 dc5415_nyu_edu dc5415_nyu_edu      11507 2023-12-06 21:43 /user/dc5415_nyu_edu/Project/Data/Format_data/lineups.parquet/part-00090-eb7d7c50-6c24-4e0d-9ec0-242782ea7493-c000.

In [102]:
pwd

'/home/dc5415_nyu_edu/Project/Code/Parsing'